# Research Question: 

Question: Can we predict the number of people who attain their bachelor's in an OECD country? 

In this assignment, we want to predict the number of people in OECD countrys that complete their Bachelor's degree. Facors like the country's GDP, ratio of people enrolled in primary education, secondary education, and tertiary education, the population of the country, how much the government spends on higher education, how much households spend on higher education, number of public universities, number of private universities, average cost of higher education, household income, and the year are all included as variables in this model. We will train a multivariate regression to see if we can reliably predict the number of people graduating with their bachelors.

Our inspiration for this project stemmed from https://icfdn.org/our-impact/education/. In this website, we found out that "Just one extra year of schooling can increase an individual’s earnings by up to 10%, and can raise the region’s average annual gross domestic product (GDP) growth by 0.37%." Because of this we wanted to explore how factors of education in a country can impact a country's GDP. 

We decided to only evaluate countries that are part of the Organization for Economic Co-operation and Development (OECD). There are 37 countries that are part of this organization that collaborate to develop policy standards and economic growth. We chose countries that are part of the OECD to evalvuate on because they account for three-fifths of the world's GDP, three-quarters of world trade, half of the world's energy consumption, and 18 percent of the world's population. Because these 37 countries account for a huge part of a country's GDP, we decided that this group of countries would be easier to evaluate compared attaining data from all 197 countries in the world.  https://www.state.gov/the-organization-for-economic-co-operation-and-development-oecd/#:~:text=and%20Development%20(OECD)-,The%20Organization%20for%20Economic%20Cooperation%20and%20Development%20(OECD),to%20promote%20sustainable%20economic%20growth.


In [316]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import duckdb 

# Data Collection/Cleaning: 

## Enrollment rates in early childhood education: 
https://data.oecd.org/students/enrolment-rate-in-early-childhood-education.htm

This data set shows the enrollment rates in early childhood education in OECD countries. The net enrollment rates are calculated by the number of students of a particular age group (ages 3-5) enrolled in early childhood education by the size of the population of that age group. This data set only includes enrollment rates from 2013-2020.

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location would specificy what country. The indicator specified what type of education that age group was enrolled in. This column would be helpful for us because when we combine all the data sets, we need to use this indicator value to differentiate what type of education they are enrolled in. The subject column listed the age group of each row (ages 3-5). The Measure column just specifies how the data was separated. Because this data set is a part of a larger Education database, the measure value just indicated how each age group was grouped by, and in this case it is age. Because the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each enrollment rate is from, ranges from years 2013 to 2020. The Value column is displays the net enrollment percentages for each row. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, I removed the Measure, Frequency, and Flag Codes columns. After removing these columns, the data set only includes the columns: Location, Indicator, Subject, Measure, Frequency, and Time. 


enrollment_early_df = pd.read_csv('enrollment rate in early childhood education.csv')
query = """
        SELECT Location, Indicator, Subject, Time, Value
        FROM enrollment_early_df
        """
enrollment_early_df = duckdb.sql(query).df()
enrollment_early_df.head()

Because, we want to figure out the enrollment rates for each year for each country, we need to combine all the age groups for each year for each country. To do this, we calculated the average enrollment rate for each country for each year. At the end, we dropped the Subject and Indicator columns because for this specific case we just need the enrollment rates, years, and country name. We also renamed all the columns to better represent the values in order to better represent the data and easier to understand. 

filtered_df = enrollment_early_df[enrollment_early_df['SUBJECT'].isin(['AGE_3', 'AGE_4', 'AGE_5'])]
enrollment_early_education_df = filtered_df.groupby(['LOCATION','TIME'])['Value'].mean().reset_index()
enrollment_early_education_df = enrollment_early_education_df.drop_duplicates()
enrollment_early_education_df = enrollment_early_education_df.rename(columns = {"LOCATION": "Country", 
                                                                                "TIME": "Year", 
                                                                               "Value" : "Early Childhood Education Enrollment Rates"})
enrollment_early_education_df = enrollment_early_education_df.replace({"ENROLMENT_ECE" : "Early Childhood"})
enrollment_early_education_df.head()

## Enrollment rates in secondary and teritiary education: 

https://data.oecd.org/students/enrolment-rate-in-secondary-and-tertiary-education.htm#indicator-chart

This data set shows the enrollment rates in secondary and tertiary education in OECD countries. The net enrollment rates are calculated by dividing the number of students of a particular age enrolled in these levels of education by the size of the population at that age (ages 17-19). The data set only includes data from 2013-2020.

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location specifies the country. The indicator specified what type of education that age group was enrolled in. This column would be helpful for us because when we combine all the data sets, we need to use this indicator value to differentiate what type of education they are enrolled in. The subject column listed the age group of each row (ages 17-19). The Measure column just specifies how the data was separated. Because this data set is a part of a larger Education database, the measure value just indicated how each age group was grouped by, and in this case it is age. Since the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each enrollment rate is from, ranges from years 2013 to 2020. The Value column is displays the net enrollment percentages for each row. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, I removed the Measure, Frequency, and Flag Codes columns. After removing these columns, the data set only includes the columns: Location, Indicator, Subject, Measure, Frequency, and Time.

enrollment_higher_df = pd.read_csv('enrollment rates in secondary and tertiary education.csv')

query = """
        SELECT Location, Indicator, Subject, Time, Value
        FROM enrollment_higher_df
        """
enrollment_higher_df = duckdb.sql(query).df()
enrollment_higher_df.head()

Because, we want to figure out the enrollment rates for each year for each country, we need to combine all the age groups for each year for each country. To do this, we calculated the average enrollment rate for each country for each year. At the end, we dropped the Subject and Indicator columns, because in this case, we just need the enrollment rates, year, and country. We also renamed all the columns to better represent the values in order to better represent the data and easier to understand. 

filtered_df = enrollment_higher_df[enrollment_higher_df['SUBJECT'].isin(['AGE_17', 'AGE_18', 'AGE_19'])]
enrollment_higher_education_df = filtered_df.groupby(['LOCATION','TIME'])['Value'].mean().reset_index()
enrollment_higher_education_df = enrollment_higher_education_df.drop_duplicates()
enrollment_higher_education_df = enrollment_higher_education_df.rename(columns = {"LOCATION": "Country", 
                                                                                "TIME": "Year", 
                                                                               "Value" : "Higher Education Enrollment Rates"})
enrollment_higher_education_df = enrollment_higher_education_df.replace({"ENROLMENT" : "Higher"})
enrollment_higher_education_df.head()

The two dataframes about enrollment rates in education are combined below, so that we will be able to have a cohesive dataframe that shows enrollment rates in early, and higher education in 37 different countries, from 2013 to 2017. 

query = """
        SELECT *
        FROM enrollment_early_education_df
        FULL JOIN enrollment_higher_education_df
        ON enrollment_early_education_df.Country = enrollment_higher_education_df.Country
        AND enrollment_early_education_df.Year = enrollment_higher_education_df.Year;
        """
enrollment_rates_df = duckdb.sql(query).df()
enrollment_rates_df

In the table, above there are a lot of missing values. Some countries might not have enrollment rates for either early childhood education or higher education and because of this a lot of Column values for Country, and Year are filled with Nan. To fix this, we have to make all the values in the Country and Country_2 column the same, and Year and Year_2 values the same. After doing this, we need to drop the Country_2 and Year_2 columns, because they are redundant and change all the float values in Year to be integers.

# Fill missing values in Country with values from Country_2
enrollment_rates_df['Country'] = enrollment_rates_df['Country'].fillna(enrollment_rates_df['Country_2'])

# Fill missing values in Country_2 with values from Country
enrollment_rates_df['Country_2'] = enrollment_rates_df['Country_2'].fillna(enrollment_rates_df['Country'])

# Fill missing values in Year with values from Year_2
enrollment_rates_df['Year'] = enrollment_rates_df['Year'].fillna(enrollment_rates_df['Year_2'])

# Fill missing values in Year_2 with values from Year
enrollment_rates_df['Year_2'] = enrollment_rates_df['Year_2'].fillna(enrollment_rates_df['Year'])

#dropping Country_2 and Year_2 columns
enrollment_rates_df = enrollment_rates_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
enrollment_rates_df['Year'] = enrollment_rates_df['Year'].astype(int)

enrollment_rates_df

enrollment_rates_df.to_csv('enrollment_rates.csv', index=False)

## GDP:

https://data.oecd.org/gdp/gross-domestic-product-gdp.htm

This data set shows the nominal Gross Domestic Product(GDP) per capita of OEPD countries in US dollars from 1960 to 2022. The Gross domestic product is the standard measure of the value added created through the production of goods and servives in a country during a certain period. While the GDP per capita can be found by diving the total GDP by its population. It also measure the inclome earned from that population, the total amount spend on a final goods and services. 

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location specifies the country. The indicator specifies what is being measured. This column is also not necessary because there is only one value being measured in this specific data set, it is redundant. The Measure column just specifies how the data was measured, in this case it was measured in US dollars. Since the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each gdp value is from from, ranges from years 1960 to 2022. The Value column displays the nominal gdp value. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, we removed the Indicator, Subject, Measure, Frequency, and Flag Codes columns. We also renamed the "Location" column as "Country" and the "Time" column as "Year" in order to be consistent with the enrollment_rates_df. We also renamed the "Value" column as "GDP in US Dollars" in order to specify the value of it, which is needed when we combine all the data sets. 

We also need to limit the years to be in between the years 2013 to 2020 in order to be consistent with the previous data sets found and limit the amount of nan in the data. 

In [317]:
gdp_df = pd.read_csv('gdp.csv')
query = """
        SELECT 
            LOCATION AS Country,
            TIME AS Year,
            Value AS "GDP per Capita"
        FROM gdp_df
        WHERE TIME IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
gdp_df = duckdb.sql(query).df()
gdp_df

Country  Year  GDP per Capita
0       AUS  1995    22442.316842
1       AUS  1996    23289.401829
2       AUS  1997    24477.413795
3       AUS  1998    25708.263828
4       AUS  1999    27139.248201
5       AUS  2000    28312.859441
6       AUS  2001    29546.415014
7       AUS  2002    30807.514079
8       AUS  2003    32391.486238
9       AUS  2004    34000.173773
10      AUS  2005    35659.125487
11      AUS  2006    37938.792079
12      AUS  2007    39687.448610
13      AUS  2008    40130.341686
14      AUS  2009    41672.923750
15      AUS  2010    42816.428960
16      AUS  2011    44440.579478
17      AUS  2012    43884.635595
18      AUS  2013    47763.215900
19      AUS  2014    47606.754929
20      AUS  2015    47226.759745
21      AUS  2016    50136.798381
22      AUS  2017    50706.489861
23      AUS  2018    53025.386896
24      AUS  2019    52785.250556
25      AUS  2020    55772.741079
26      AUT  1995    23698.103090
27      AUT  1996    24560.615338
28      AUT  1997    25426.661912
29      AUT  1998    26675.649686
30      AUT  1999    27606.484243
31      AUT  2000    29381.672832
32      AUT  2001    29708.489450
33      AUT  2002    31178.051444
34      AUT  2003    32158.459529
35      AUT  2004    33784.446804
36      AUT  2005    35024.557484
37      AUT  2006    37662.888035
38      AUT  2007    39437.038795
39      AUT  2008    41316.022642
40      AUT  2009    40927.556365
41      AUT  2010    42019.005887
42      AUT  2011    44469.209642
43      AUT  2012    46477.655075
44      AUT  2013    47936.677963
45      AUT  2014    48813.534409
46      AUT  2015    49942.056293
47      AUT  2016    52665.087457
48      AUT  2017    54188.360666
49      AUT  2018    56956.110562
50      AUT  2019    59716.251399
51      AUT  2020    57235.673886
52      BEL  1995    22447.051902
53      BEL  1996    22743.894711
54      BEL  1997    23732.789845
55      BEL  1998    24369.501242
56      BEL  1999    25441.891387
57      BEL  2000    27790.606306
58      BEL  2001    28792.401342
59      BEL  2002    30281.667989
60      BEL  2003    30934.823303
61      BEL  2004    32063.687224
62      BEL  2005    33176.680884
63      BEL  2006    35256.775979
64      BEL  2007    36794.811405
65      BEL  2008    37883.233422
66      BEL  2009    37751.634063
67      BEL  2010    39836.533412
68      BEL  2011    40943.343479
69      BEL  2012    42290.477674
70      BEL  2013    43672.712292
71      BEL  2014    44929.933328
72      BEL  2015    46201.685891
73      BEL  2016    48599.202676
74      BEL  2017    50442.947518
75      BEL  2018    52530.841510
76      BEL  2019    55804.713631
77      BEL  2020    54544.419240
78      CAN  1995    23485.643444
79      CAN  1996    24050.176142
80      CAN  1997    25259.725362
81      CAN  1998    26319.930258
82      CAN  1999    27841.629576
83      CAN  2000    29362.289573
84      CAN  2001    30231.005032
85      CAN  2002    30963.222007
86      CAN  2003    32350.070882
87      CAN  2004    33925.892560
88      CAN  2005    36327.662059
89      CAN  2006    38120.176792
90      CAN  2007    39575.324973
91      CAN  2008    40376.330167
92      CAN  2009    38865.406022
93      CAN  2010    40099.497886
94      CAN  2011    41666.718851
95      CAN  2012    42290.879082
96      CAN  2013    44298.514462
97      CAN  2014    45753.782936
98      CAN  2015    44670.054374
99      CAN  2016    46472.368771
100     CAN  2017    48317.191163
101     CAN  2018    49992.811418
102     CAN  2019    49832.414539
103     CAN  2020    47226.357276
104     CZE  1995    13855.325028
105     CZE  1996    14689.582503
106     CZE  1997    14825.328950
107     CZE  1998    14977.240849
108     CZE  1999    15397.922823
109     CZE  2000    16211.043497
110     CZE  2001    17611.358497
111     CZE  2002    18245.669005
112     CZE  2003    19524.399624
113     CZE  2004    20912.054683
114     CZE  2005    22045.998880
115     CZE  2006    23857.518264
116     CZE  2007    26224

In [318]:
gdp_df.to_csv('clean_gdp.csv', index=False)

The two dataframes (enrollment_rates_df and gdp_df) are combined below using a Full Join, so that we will have a cohesive data frame showing enrollment rates and gdp of each country from 2013-2020. 

query = """
        SELECT *
        FROM enrollment_rates_df
        FULL JOIN gdp_df
        ON enrollment_rates_df.Country = gdp_df.Country
        AND enrollment_rates_df.Year = gdp_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df 

In the table, above there are a lot of missing values. Some countries might not have enrollment rates for either early childhood education or higher education or gdp values and because of this a lot of Column values for Country, and Year are filled with Nan. To fix this, we have to make all the values in the Country and Country_2 column the same, and Year and Year_2 values the same. After doing this, we need to drop the Country_2 and Year_2 columns, because they are redundant, change all the float values in Year to be integers, and round the GDP values to two decimals to represent US dollars. 

# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

#rounding the GDP values to 2 decimals
combined_df['GDP per Capita'] = combined_df['GDP per Capita'].round(2)

combined_df

## Population:

https://data.oecd.org/pop/population.htm

This data set shows the total population of OECD country in millions of people from 1950 to 2022. The total population includes the following: national armed forces stationed abroad; merchant seamen at sea; diplomatic personnel located abroad; civilian aliens resident in the country; displaced persons resident in the country. However, it excludes the following: foreign armed forces stationed in the country; foreign diplomatic personnel located in the country; civilian aliens temporarily in the country.

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location specifies the country. The indicator specifies what is being measured (population). This column is also not necessary because there is only one value being measured in this specific data set, it is redundant. The Measure column just specifies how the data was measured, in this case it is the population per millions of people. Since the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each gdp value is from from, ranges from years 1950 to 2022. The Value column displays the total population per millions of people. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, we removed the Indicator, Subject, Measure, Frequency, and Flag Codes columns. We also renamed the "Location" column as "Country" and the "Time" column as "Year" in order to be consistent with the enrollment_rates_df. We also renamed the "Value" column as "Population" in order to specify the value of it, which is needed when we combine all the data sets. 

We also need to limit Years to be in between 2013 to 2020 in order to be consistent with the previous data sets and limit the amount of missing values. 

In [319]:
population_df = pd.read_csv('population.csv')
population_df

query = """
        SELECT 
            LOCATION AS Country,
            TIME AS Year,
            Value * 1000000 AS "Total Population"
        FROM population_df
        WHERE TIME IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
population_df = duckdb.sql(query).df()
population_df

Country  Year  Total Population
0        AUS  1995        18004882.0
1        AUS  1996        18224767.0
2        AUS  1997        18423037.0
3        AUS  1998        18607584.0
4        AUS  1999        18812264.0
...      ...   ...               ...
1009     LTU  2016         2868231.0
1010     LTU  2017         2828403.0
1011     LTU  2018         2801543.0
1012     LTU  2019         2794137.0
1013     LTU  2020         2794885.0

[1014 rows x 3 columns]

In [320]:
population_df.to_csv('clean_population.csv', index=False)

The two dataframes (combined_df and population_df) are combined below using a Full Join, so that we will have a cohesive data frame showing enrollment rates, gdp, and total population of each country from 2013-2020.

In [321]:
query = """
        SELECT *
        FROM gdp_df
        FULL JOIN population_df
        ON gdp_df.Country = population_df.Country
        AND gdp_df.Year = population_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df 

Country    Year  GDP per Capita Country_2  Year_2  Total Population
0        AUS  1995.0    22442.316842       AUS    1995      1.800488e+07
1        AUS  1996.0    23289.401829       AUS    1996      1.822477e+07
2        AUS  1997.0    24477.413795       AUS    1997      1.842304e+07
3        AUS  1998.0    25708.263828       AUS    1998      1.860758e+07
4        AUS  1999.0    27139.248201       AUS    1999      1.881226e+07
...      ...     ...             ...       ...     ...               ...
1009     NaN     NaN             NaN      OECD    2000      1.200935e+09
1010     NaN     NaN             NaN      OECD    2010      1.292202e+09
1011     NaN     NaN             NaN      OECD    2015      1.330543e+09
1012     NaN     NaN             NaN      OECD    2014      1.322342e+09
1013     NaN     NaN             NaN      OECD    2018      1.354855e+09

[1014 rows x 6 columns]

In the table, above there are a lot of missing values. Some countries might not have enrollment rates for either early childhood education or higher education or gdp values and because of this a lot of Column values for Country, and Year are filled with Nan. To fix this, we have to make all the values in the Country and Country_2 column the same, and Year and Year_2 values the same. After doing this, we need to drop the Country_2 and Year_2 columns, because they are redundant and change all the float values in Year to be integers, 

In [322]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df

Country  Year  GDP per Capita  Total Population
0        AUS  1995    22442.316842      1.800488e+07
1        AUS  1996    23289.401829      1.822477e+07
2        AUS  1997    24477.413795      1.842304e+07
3        AUS  1998    25708.263828      1.860758e+07
4        AUS  1999    27139.248201      1.881226e+07
...      ...   ...             ...               ...
1009    OECD  2000             NaN      1.200935e+09
1010    OECD  2010             NaN      1.292202e+09
1011    OECD  2015             NaN      1.330543e+09
1012    OECD  2014             NaN      1.322342e+09
1013    OECD  2018             NaN      1.354855e+09

[1014 rows x 4 columns]

## Public Spending On Education:

https://data.oecd.org/eduresource/public-spending-on-education.htm#indicator-chart

This data shows the public spending on education as a percentage fo GDP for tertiary levels of education. Public spending on education includes direct expendiute on educational institutions, as well as education-related public susidies given to households and administered by educational institutions. Public entities include ministries other than ministries of education, local and regional governments, and other public agencies. Public spending includes expenditure on schools, universities and other public and private institutions delivering or supporting educational services. 

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location specifies the country. The indicator specifies what is being measured (public spending on education). This column is also not necessary because there is only one value being measured in this specific data set, it is redundant. The Measure column just specifies how the data was measured, in this case it is the public spending as a percentage of gdp. Since the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each gdp value is from from, ranges from years 2000 to 2020. The Value column displays the percentage of gdp that is used for public education. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, we removed the Indicator, Subject, Measure, Frequency, and Flag Codes columns. We also renamed the "Location" column as "Country" and the "Time" column as "Year" in order to be consistent with the enrollment_rates_df. We also renamed the "Value" column as "Public Spending on Education" in order to specify the value of it, which is needed when we combine all the data sets.

We also need to limit Years to be in between 2013 to 2020 in order to be consistent with the previous data sets and limit the amount of missing values.

In [323]:
public_spending_df = pd.read_csv('public_spending_on_education.csv')

query = """
        SELECT 
            LOCATION AS Country,
            TIME AS Year,
            Value AS "Public Spending on Education (%)"
        FROM public_spending_df
        WHERE TIME IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
public_spending_df = duckdb.sql(query).df()
public_spending_df

Country  Year  Public Spending on Education (%)
0       AUS  2000                          0.744540
1       AUS  2005                          0.689385
2       AUS  2008                          0.689400
3       AUS  2009                          0.734759
4       AUS  2010                          0.778470
5       AUS  2011                          0.743412
6       AUS  2013                          0.718812
7       AUS  2014                          0.717300
8       AUS  2015                          0.769290
9       AUS  2016                          0.756591
10      AUS  2017                          0.729282
11      AUS  2018                          0.656634
12      AUS  2019                          0.647559
13      AUS  2020                          0.680441
14      AUT  2013                          1.644516
15      AUT  2014                          1.614541
16      AUT  2015                          1.634081
17      AUT  2016                          1.631474
18      AUT  2017                          1.560725
19      AUT  2018                          1.552325
20      AUT  2019                          1.557053
21      AUT  2020                          1.637095
22      BEL  2005                          1.089700
23      BEL  2008                          1.128475
24      BEL  2009                          1.226435
25      BEL  2010                          1.208465
26      BEL  2011                          1.214926
27      BEL  2013                          1.276725
28      BEL  2014                          1.267146
29      BEL  2015                          1.221587
30      BEL  2016                          1.231372
31      BEL  2017                          1.252936
32      BEL  2018                          1.269149
33      BEL  2019                          1.277785
34      BEL  2020                          1.373827
35      CAN  2000                          1.485331
36      CAN  2005                          1.338613
37      CAN  2008                          1.524971
38      CAN  2009                          1.480583
39      CAN  2010                          1.578337
40      CAN  2011                          1.426457
41      CAN  2013                          1.281192
42      CAN  2014                          1.238263
43      CAN  2015                          1.199260
44      CAN  2016                          1.249911
45      CAN  2017                          1.248397
46      CAN  2018                          1.217149
47      CAN  2019                          1.169387
48      CAN  2020                          1.210443
49      CZE  1995                          0.586523
50      CZE  2000                          0.631571
51      CZE  2005                          0.764700
52      CZE  2008                          0.840469
53      CZE  2009                          0.935620
54      CZE  2010                          0.885381
55      CZE  2011                          1.077835
56      CZE  2013                          0.851949
57      CZE  2014                          0.777844
58      CZE  2015                          0.751153
59      CZE  2016                          0.684558
60      CZE  2017                          0.681298
61      CZE  2018                          0.909412
62      CZE  2019                          0.916513
63      CZE  2020                          0.847111
64      DNK  1995                          1.593177
65      DNK  2000                          1.482842
66      DNK  2005                          1.603695
67      DNK  2008                          1.515695
68      DNK  2009                          1.701416
69      DNK  2010                          1.687580
70      DNK  2011                          1.695767
71      DNK  2013                          1.540204
72      DNK  2014                          1.562260
73      DNK  2016                          1.786348
74      DNK  2017                          1.587298
75      DNK  2018                          1.595249


In [324]:
public_spending_df.to_csv('clean_public_education_df.csv', index=False)

The two dataframes (combined_df and public_spending_df) are combined below using a Full Join, so that we will have a cohesive data frame showing enrollment rates, gdp, and total population, and public spending as a percentage of gdp of each country from 2013-2020.

In [325]:
query = """
        SELECT *
        FROM combined_df
        FULL JOIN public_spending_df
        ON combined_df.Country = public_spending_df.Country
        AND combined_df.Year = public_spending_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df 

Country    Year  GDP per Capita  Total Population Country_2  Year_2  \
0        AUS  2000.0    28312.859441        19028802.0       AUS  2000.0   
1        AUS  2005.0    35659.125487        20176844.0       AUS  2005.0   
2        AUS  2008.0    40130.341686        21249199.0       AUS  2008.0   
3        AUS  2009.0    41672.923750        21691653.0       AUS  2009.0   
4        AUS  2010.0    42816.428960        22031750.0       AUS  2010.0   
...      ...     ...             ...               ...       ...     ...   
1019     NaN     NaN             NaN               NaN       RUS  2017.0   
1020     NaN     NaN             NaN               NaN       RUS  2010.0   
1021     NaN     NaN             NaN               NaN       RUS  2015.0   
1022     NaN     NaN             NaN               NaN       RUS  2014.0   
1023     NaN     NaN             NaN               NaN       RUS  2018.0   

      Public Spending on Education (%)  
0                             0.744540  
1                             0.689385  
2                             0.689400  
3                             0.734759  
4                             0.778470  
...                                ...  
1019                          0.547857  
1020                          0.971791  
1021                          0.734968  
1022                          0.811595  
1023                          0.652231  

[1024 rows x 7 columns]

In the table, above there are a lot of missing values. Some countries might not have enrollment rates for either early childhood education or higher education or gdp values, or etc. and because of this a lot of Column values for Country, and Year are filled with Nan. To fix this, we have to make all the values in the Country and Country_2 column the same, and Year and Year_2 values the same. After doing this, we need to drop the Country_2 and Year_2 columns, because they are redundant and change all the float values in Year to be integers,

In [326]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df

Country  Year  GDP per Capita  Total Population  \
0        AUS  2000    28312.859441        19028802.0   
1        AUS  2005    35659.125487        20176844.0   
2        AUS  2008    40130.341686        21249199.0   
3        AUS  2009    41672.923750        21691653.0   
4        AUS  2010    42816.428960        22031750.0   
...      ...   ...             ...               ...   
1019     RUS  2017             NaN               NaN   
1020     RUS  2010             NaN               NaN   
1021     RUS  2015             NaN               NaN   
1022     RUS  2014             NaN               NaN   
1023     RUS  2018             NaN               NaN   

      Public Spending on Education (%)  
0                             0.744540  
1                             0.689385  
2                             0.689400  
3                             0.734759  
4                             0.778470  
...                                ...  
1019                          0.547857  
1020                          0.971791  
1021                          0.734968  
1022                          0.811595  
1023                          0.652231  

[1024 rows x 5 columns]

## Private Spending on Education:

https://data.oecd.org/eduresource/private-spending-on-education.htm#indicator-chart

This data shows private spending on education as a percentage of GDP for tertiary education. Private spending on education refers to expenditure funded by private resources which are households and other private entities. It includes all direct expenditure on education institions, and net of public subsidies.

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location specifies the country. The indicator specifies what is being measured (private spending on education). This column is also not necessary because there is only one value being measured in this specific data set, it is redundant. The Measure column just specifies how the data was measured, in this case it is the public spending as a percentage of gdp. Since the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each gdp value is from from, ranges from years 2000 to 2020. The Value column displays the percentage of gdp that is used for public education. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, we removed the Indicator, Subject, Measure, Frequency, and Flag Codes columns. We also renamed the "Location" column as "Country" and the "Time" column as "Year" in order to be consistent with the enrollment_rates_df. We also renamed the "Value" column as "Private Spending on Education (%)" in order to specify the value of it, which is needed when we combine all the data sets.

We also need to limit Years to be in between 2013 to 2020 in order to be consistent with the previous data sets and limit the amount of missing values.

In [327]:
private_spending_df = pd.read_csv('private_spending_on_education.csv')

query = """
        SELECT 
            LOCATION AS Country,
            TIME AS Year,
            Value AS "Private Spending on Education (%)"
        FROM private_spending_df
        WHERE TIME IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
private_spending_df = duckdb.sql(query).df()
private_spending_df

Country  Year  Private Spending on Education (%)
0       AUS  2000                           0.748428
1       AUS  2005                           0.828712
2       AUS  2008                           0.844496
3       AUS  2009                           0.882858
4       AUS  2010                           0.896708
5       AUS  2011                           0.885928
6       AUS  2012                           0.881156
7       AUS  2013                           0.972901
8       AUS  2014                           1.133321
9       AUS  2015                           1.264779
10      AUS  2016                           1.157713
11      AUS  2017                           1.287303
12      AUS  2018                           1.230631
13      AUS  2019                           1.275049
14      AUS  2020                           1.195328
15      AUT  2012                           0.084814
16      AUT  2013                           0.094167
17      AUT  2014                           0.095220
18      AUT  2015                           0.108589
19      AUT  2016                           0.112024
20      AUT  2017                           0.152499
21      AUT  2018                           0.182909
22      AUT  2019                           0.192745
23      AUT  2020                           0.184251
24      BEL  2005                           0.110690
25      BEL  2008                           0.125309
26      BEL  2009                           0.138248
27      BEL  2010                           0.135787
28      BEL  2011                           0.133809
29      BEL  2012                           0.188122
30      BEL  2013                           0.198055
31      BEL  2014                           0.201945
32      BEL  2015                           0.199652
33      BEL  2016                           0.214842
34      BEL  2017                           0.211221
35      BEL  2018                           0.201000
36      BEL  2019                           0.190041
37      BEL  2020                           0.211679
38      CAN  2000                           0.949047
39      CAN  2005                           1.092758
40      CAN  2008                           0.900250
41      CAN  2009                           1.136901
42      CAN  2010                           1.172812
43      CAN  2011                           1.172401
44      CAN  2012                           0.923423
45      CAN  2013                           0.989400
46      CAN  2014                           1.006665
47      CAN  2015                           0.920499
48      CAN  2016                           1.096771
49      CAN  2017                           1.065671
50      CAN  2018                           1.108418
51      CAN  2019                           1.008947
52      CAN  2020                           1.154651
53      CZE  1995                           0.233220
54      CZE  2000                           0.107703
55      CZE  2005                           0.177054
56      CZE  2008                           0.221858
57      CZE  2009                           0.235089
58      CZE  2010                           0.237878
59      CZE  2011                           0.251808
60      CZE  2012                           0.254275
61      CZE  2013                           0.254183
62      CZE  2014                           0.243058
63      CZE  2015                           0.228737
64      CZE  2016                           0.222914
65      CZE  2017                           0.215420
66      CZE  2018                           0.208209
67      CZE  2019                           0.199990
68      CZE  2020                           0.204956
69      DNK  1995                           0.009551
70      DNK  2000                           0.036250
71      DNK  2005                           0.054630
72      DNK  2008                           0.070842
73      DNK  2009                           0.081490
74      DNK  2010            

In [328]:
private_spending_df.to_csv('clean_private_education_df.csv', index=False)

The two dataframes (combined_df and private_spending_df) are combined below using a Full Join, so that we will have a cohesive data frame showing enrollment rates, gdp, and total population, and public spending as a percentage of GDP, and private spending as a percentage of GDP of each country from 2013-2020.

In [329]:
query = """
        SELECT *
        FROM combined_df
        FULL JOIN private_spending_df
        ON combined_df.Country = private_spending_df.Country
        AND combined_df.Year = private_spending_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df 

Country    Year  GDP per Capita  Total Population  \
0        AUS  2000.0    28312.859441        19028802.0   
1        AUS  2005.0    35659.125487        20176844.0   
2        AUS  2008.0    40130.341686        21249199.0   
3        AUS  2009.0    41672.923750        21691653.0   
4        AUS  2010.0    42816.428960        22031750.0   
...      ...     ...             ...               ...   
1020     NLD  2008.0    46419.042594        16445590.0   
1021     NLD  2016.0    52289.404292        17030314.0   
1022     SVK  1995.0     8695.696416         5363676.0   
1023     ISR  2017.0    39352.294675         8713268.0   
1024     NaN     NaN             NaN               NaN   

      Public Spending on Education (%) Country_2  Year_2  \
0                             0.744540       AUS  2000.0   
1                             0.689385       AUS  2005.0   
2                             0.689400       AUS  2008.0   
3                             0.734759       AUS  2009.0   
4                             0.778470       AUS  2010.0   
...                                ...       ...     ...   
1020                          0.998374       NLD  2008.0   
1021                          1.143769       NLD  2016.0   
1022                          0.687322       SVK  1995.0   
1023                          0.792850       ISR  2017.0   
1024                               NaN       RUS  2012.0   

      Private Spending on Education (%)  
0                              0.748428  
1                              0.828712  
2                              0.844496  
3                              0.882858  
4                              0.896708  
...                                 ...  
1020                           0.398858  
1021                           0.498491  
1022                           0.033159  
1023                           0.562843  
1024                           0.461101  

[1025 rows x 8 columns]

In the table, above there are a lot of missing values. Some countries might not have enrollment rates for either early childhood education or higher education or gdp values, or etc. and because of this a lot of Column values for Country, and Year are filled with Nan. To fix this, we have to make all the values in the Country and Country_2 column the same, and Year and Year_2 values the same. After doing this, we need to drop the Country_2 and Year_2 columns, because they are redundant and change all the float values in Year to be integers,

In [330]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df

Country  Year  GDP per Capita  Total Population  \
0        AUS  2000    28312.859441        19028802.0   
1        AUS  2005    35659.125487        20176844.0   
2        AUS  2008    40130.341686        21249199.0   
3        AUS  2009    41672.923750        21691653.0   
4        AUS  2010    42816.428960        22031750.0   
...      ...   ...             ...               ...   
1020     NLD  2008    46419.042594        16445590.0   
1021     NLD  2016    52289.404292        17030314.0   
1022     SVK  1995     8695.696416         5363676.0   
1023     ISR  2017    39352.294675         8713268.0   
1024     RUS  2012             NaN               NaN   

      Public Spending on Education (%)  Private Spending on Education (%)  
0                             0.744540                           0.748428  
1                             0.689385                           0.828712  
2                             0.689400                           0.844496  
3                             0.734759                           0.882858  
4                             0.778470                           0.896708  
...                                ...                                ...  
1020                          0.998374                           0.398858  
1021                          1.143769                           0.498491  
1022                          0.687322                           0.033159  
1023                          0.792850                           0.562843  
1024                               NaN                           0.461101  

[1025 rows x 6 columns]

## Household Income per Capita:

https://data.oecd.org/hha/household-disposable-income.htm#indicator-chart

This data set shows the gross household disposable income per capita in 37 OECD countries. Household disposable income is available to households such as wages and salaries, income from self-employment and unincorporated enterprices, income from pensions and other social benefits, and income from financial investments. Gross means that depreciation costs are not subtracted. For gross household disposable income per capita, growth rates (percentage change from previous period) are presented; these are ‘real’ growth rates adjusted to remove the effects of price changes. Information is also presented for gross household disposable income including social transfers, such as health or education provided for free or at reduced prices by governments and not-for-profit organisations. 

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location specifies the country. The indicator specifies what is being measured (household disposable income). This column is also not necessary because there is only one value being measured in this specific data set, it is redundant. The Measure column just specifies how the data was measured, in this case it is the household income per capita. Since the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each gdp value is from from, ranges from years 1970 to 2020. The Value column displays the percentage of gdp that is used for public education. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, we removed the Indicator, Subject, Measure, Frequency, and Flag Codes columns. We also renamed the "Location" column as "Country" and the "Time" column as "Year" in order to be consistent with the enrollment_rates_df. We also renamed the "Value" column as "Household Income per Capita" in order to specify the value of it, which is needed when we combine all the data sets.

We also need to limit Years to be in between 2013 to 2020 in order to be consistent with the previous data sets and limit the amount of missing values.

In [331]:
household_income_df = pd.read_csv('household_income.csv')

query = """
        SELECT 
            LOCATION AS Country,
            TIME AS Year,
            Value AS "Household Income per Capita"
        FROM household_income_df
        WHERE TIME IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
household_income_df = duckdb.sql(query).df()
household_income_df

Country  Year  Household Income per Capita
0       JPN  2007                 24916.381131
1       JPN  2008                 25393.938874
2       JPN  2009                 25581.218842
3       JPN  2010                 26402.021262
4       JPN  2011                 27299.673602
5       JPN  2012                 28447.427703
6       JPN  2013                 30474.352272
7       JPN  2014                 30032.209494
8       JPN  2015                 30597.027634
9       JPN  2016                 29290.345599
10      JPN  2017                 29915.592624
11      JPN  2018                 30777.441353
12      JPN  2019                 30918.213957
13      JPN  2020                 32673.060729
14      NLD  2007                 29186.943217
15      NLD  2008                 30385.764825
16      NLD  2009                 30119.921801
17      NLD  2010                 29940.808487
18      NLD  2011                 30360.104181
19      NLD  2012                 31072.643726
20      NLD  2013                 31685.554446
21      NLD  2014                 31934.998701
22      NLD  2015                 32193.957442
23      NLD  2016                 33258.289148
24      NLD  2017                 34379.958130
25      NLD  2018                 36263.623111
26      NLD  2019                 38038.638269
27      NLD  2020                 39703.217498
28      CZE  2007                 16992.203677
29      CZE  2008                 17934.526047
30      CZE  2009                 18629.118702
31      CZE  2010                 19246.263927
32      CZE  2011                 19394.281379
33      CZE  2012                 19842.068091
34      CZE  2013                 20841.747191
35      CZE  2014                 21889.796443
36      CZE  2015                 22313.393223
37      CZE  2016                 23663.665288
38      CZE  2017                 25424.300200
39      CZE  2018                 26770.884332
40      CZE  2019                 28746.850902
41      CZE  2020                 29167.702791
42      DEU  2007                 27926.104851
43      DEU  2008                 29093.343127
44      DEU  2009                 29162.206452
45      DEU  2010                 30704.558252
46      DEU  2011                 32107.492697
47      DEU  2012                 33295.390627
48      DEU  2013                 34223.523781
49      DEU  2014                 35129.686978
50      DEU  2015                 35492.396434
51      DEU  2016                 37893.961855
52      DEU  2017                 39272.160169
53      DEU  2018                 41169.929877
54      DEU  2019                 42752.835599
55      DEU  2020                 43760.281364
56      GRC  2007                 22952.814242
57      GRC  2008                 24398.728059
58      GRC  2009                 24535.085959
59      GRC  2010                 22097.889580
60      GRC  2011                 20129.685396
61      GRC  2012                 18709.575912
62      GRC  2013                 18672.503700
63      GRC  2014                 19285.921114
64      GRC  2015                 19593.336403
65      GRC  2016                 20285.622896
66      GRC  2017                 20670.295757
67      GRC  2018                 21202.732907
68      GRC  2019                 22824.596800
69      GRC  2020                 22156.814520
70      PRT  2007                 20045.299165
71      PRT  2008                 20962.280240
72      PRT  2009                 21057.697770
73      PRT  2010                 21540.899246
74      PRT  2011                 20912.361863
75      PRT  2012                 20930.664090
76      PRT  2013                 21837.328953
77      PRT  2014                 21837.831140
78      PRT  2015                 22627.671907
79      PRT  2016                 23946.102158
80      PRT  2017                 24508.127206
81      PRT  2018                 26052.469172
82      PRT  2019                 27747.043975
83      PRT  2020                 27334.194239
84      A

In [332]:
household_income_df.to_csv('clean_household_income_df.csv', index=False)

The two dataframes (combined_df and household_income_df) are combined below using a Full Join, so that we will have a cohesive data frame showing enrollment rates, gdp, and total population, public spending as a percentage of GDP, private spending as a percentage of GDP, and household income per capita of each country from 2013-2020.

In [333]:
query = """
        SELECT *
        FROM combined_df
        FULL JOIN household_income_df
        ON combined_df.Country = household_income_df.Country
        AND combined_df.Year = household_income_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df 

Country  Year  GDP per Capita  Total Population  \
0        AUS  2008    40130.341686        21249199.0   
1        AUS  2009    41672.923750        21691653.0   
2        AUS  2010    42816.428960        22031750.0   
3        AUS  2011    44440.579478        22340024.0   
4        AUS  2014    47606.754929        23475686.0   
...      ...   ...             ...               ...   
1020     ESP  2008    33242.245427        45983169.0   
1021     USA  2011    49951.907651       311583481.0   
1022     EST  2015    29222.748082         1314608.0   
1023     NLD  2016    52289.404292        17030314.0   
1024     USA  2008    48498.445211       304093966.0   

      Public Spending on Education (%)  Private Spending on Education (%)  \
0                             0.689400                           0.844496   
1                             0.734759                           0.882858   
2                             0.778470                           0.896708   
3                             0.743412                           0.885928   
4                             0.717300                           1.133321   
...                                ...                                ...   
1020                          0.941829                           0.252409   
1021                          1.065658                           1.661183   
1022                          1.241348                           0.417253   
1023                          1.143769                           0.498491   
1024                          1.049673                           1.490560   

     Country_2  Year_2  Household Income per Capita  
0          AUS  2008.0                 31051.323158  
1          AUS  2009.0                 30789.699428  
2          AUS  2010.0                 32599.998578  
3          AUS  2011.0                 33941.087440  
4          AUS  2014.0                 36816.129278  
...        ...     ...                          ...  
1020       ESP  2008.0                 23317.348626  
1021       USA  2011.0                 42186.856901  
1022       EST  2015.0                 19321.329148  
1023       NLD  2016.0                 33258.289148  
1024       USA  2008.0                 40004.983201  

[1025 rows x 9 columns]

In the table, above there are a lot of missing values. Some countries might not have enrollment rates for either early childhood education or higher education or gdp values, or etc. and because of this a lot of Column values for Country, and Year are filled with Nan. To fix this, we have to make all the values in the Country and Country_2 column the same, and Year and Year_2 values the same. After doing this, we need to drop the Country_2 and Year_2 columns, because they are redundant and change all the float values in Year to be integers.

In [334]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df

Country  Year  GDP per Capita  Total Population  \
0        AUS  2008    40130.341686        21249199.0   
1        AUS  2009    41672.923750        21691653.0   
2        AUS  2010    42816.428960        22031750.0   
3        AUS  2011    44440.579478        22340024.0   
4        AUS  2014    47606.754929        23475686.0   
...      ...   ...             ...               ...   
1020     ESP  2008    33242.245427        45983169.0   
1021     USA  2011    49951.907651       311583481.0   
1022     EST  2015    29222.748082         1314608.0   
1023     NLD  2016    52289.404292        17030314.0   
1024     USA  2008    48498.445211       304093966.0   

      Public Spending on Education (%)  Private Spending on Education (%)  \
0                             0.689400                           0.844496   
1                             0.734759                           0.882858   
2                             0.778470                           0.896708   
3                             0.743412                           0.885928   
4                             0.717300                           1.133321   
...                                ...                                ...   
1020                          0.941829                           0.252409   
1021                          1.065658                           1.661183   
1022                          1.241348                           0.417253   
1023                          1.143769                           0.498491   
1024                          1.049673                           1.490560   

      Household Income per Capita  
0                    31051.323158  
1                    30789.699428  
2                    32599.998578  
3                    33941.087440  
4                    36816.129278  
...                           ...  
1020                 23317.348626  
1021                 42186.856901  
1022                 19321.329148  
1023                 33258.289148  
1024                 40004.983201  

[1025 rows x 7 columns]

## Education Spending:

https://data.oecd.org/eduresource/education-spending.htm#indicator-chart

This data set shows the average amount of education spending that covers expenditure on schools, universities and other public and private educational institutions in 37 OECD countries. Spending includes instruction and ancillary services for students and families provided through educational institutions. Education spending is shown in USD per student.

The original data set has 8 different columns: Location, Indicator, Subject, Measure, Frequency, Time, Value, Flag Codes). The Location specifies the country. The indicator specifies what is being measured (education spending in dollars). This column is also not necessary because there is only one value being measured in this specific data set, it is redundant. The Measure column just specifies how the data was measured, in this case it is the USD per student. Since the Measure is the same for all the rows, this column isn't necessary. The frequency column is similar to the Measure column and is also not necessary for this case. The Time column indicates what year each gdp value is from from, ranges from years 1995 to 2020. The Value column displays the percentage of gdp that is used for public education. And the last column, Flag Codes, is used for indicating something wrong for each row, in this case, because the whole column does not contain any values, this column is not necessary.

From the original data set, we removed the Indicator, Subject, Measure, Frequency, and Flag Codes columns. We also renamed the "Location" column as "Country" and the "Time" column as "Year" in order to be consistent with the enrollment_rates_df. We also renamed the "Value" column as "Average Spending on Higher Education (USD/student)" in order to specify the value of it, which is needed when we combine all the data sets.

We also need to limit Years to be in between 2013 to 2020 in order to be consistent with the previous data sets and limit the amount of missing values.

In [335]:
average_spending_df = pd.read_csv('educaion_spending.csv')

query = """
        SELECT 
            LOCATION AS Country,
            TIME AS Year,
            Value AS "Average Spending on Higher Education (USD/student)"
        FROM average_spending_df
        WHERE TIME IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
average_spending_df = duckdb.sql(query).df()
average_spending_df

Country  Year  Average Spending on Higher Education (USD/student)
0       AUT  2012                                         16475.7000 
1       AUT  2013                                         16853.0000 
2       AUT  2014                                         16867.6200 
3       AUT  2015                                         17560.6200 
4       AUT  2016                                         18625.0000 
5       AUT  2017                                         18974.7500 
6       AUT  2018                                         20416.6200 
7       AUT  2019                                         21946.2300 
8       AUT  2020                                         21753.4610 
9       CZE  1995                                          7846.0600 
10      CZE  2000                                          5320.9350 
11      CZE  2005                                          6572.1620 
12      CZE  2008                                          8179.3230 
13      CZE  2009                                          8403.4610 
14      CZE  2010                                          7953.9110 
15      CZE  2011                                          9478.2440 
16      CZE  2012                                         10421.6100 
17      CZE  2013                                         10307.6600 
18      CZE  2014                                         10490.2600 
19      CZE  2015                                         10960.2400 
20      CZE  2016                                         10193.6400 
21      CZE  2017                                         11440.4700 
22      CZE  2018                                         16148.1200 
23      CZE  2019                                         17962.6000 
24      CZE  2020                                         16237.3300 
25      FRA  2005                                         11188.6500 
26      FRA  2008                                         14324.2500 
27      FRA  2009                                         14931.1300 
28      FRA  2010                                         15144.2000 
29      FRA  2011                                         15585.4900 
30      FRA  2012                                         15392.0900 
31      FRA  2013                                         16233.8800 
32      FRA  2014                                         16353.8000 
33      FRA  2015                                         16257.1500 
34      FRA  2016                                         16477.1600 
35      FRA  2017                                         16870.7300 
36      FRA  2018                                         17403.7400 
37      FRA  2019                                         18702.5100 
38      FRA  2020                                         18879.8690 
39      HUN  1995                                          6369.8950 
40      HUN  2000                                          6197.4340 
41      HUN  2012                                          9039.3900 
42      HUN  2013                                         10373.9700 
43      HUN  2014                                          8647.3300 
44      HUN  2015                                          8815.0570 
45      HUN  2016                                         11508.3800 
46      HUN  2017                                         12719.9300 
47      HUN  2018                                         13759.2200 
48      HUN  2019                                         12478.0900 
49      HUN  2020                                         12097.7500 
50      CHL  1995                                          4452.8050 
51      CHL  2000                                          5875.6670 
52      CHL  2005                                          5968.9810 
53      CHL  2008                                          6384.5600 
54      CHL  2009                                          6233.5660 
55      CHL  2010                                          7159.5240 
56      CHL  2

In [336]:
average_spending_df.to_csv('clean_average_spending_df.csv', index=False)

The two dataframes (combined_df and average_spending_df) are combined below using a Full Join, so that we will have a cohesive data frame showing enrollment rates, gdp, and total population, public spending as a percentage of GDP, private spending as a percentage of GDP, household income per capita, and average spending for higher education per student of each country from 2013-2020.

In [337]:
query = """
        SELECT *
        FROM combined_df
        FULL JOIN average_spending_df
        ON combined_df.Country = average_spending_df.Country
        AND combined_df.Year = average_spending_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df 

Country  Year  GDP per Capita  Total Population  \
0        AUS  2008    40130.341686        21249199.0   
1        AUS  2009    41672.923750        21691653.0   
2        AUS  2010    42816.428960        22031750.0   
3        AUS  2011    44440.579478        22340024.0   
4        AUS  2014    47606.754929        23475686.0   
...      ...   ...             ...               ...   
1020     EST  2015    29222.748082         1314608.0   
1021     NLD  2016    52289.404292        17030314.0   
1022     USA  2008    48498.445211       304093966.0   
1023     SVK  1995     8695.696416         5363676.0   
1024     ISR  2017    39352.294675         8713268.0   

      Public Spending on Education (%)  Private Spending on Education (%)  \
0                             0.689400                           0.844496   
1                             0.734759                           0.882858   
2                             0.778470                           0.896708   
3                             0.743412                           0.885928   
4                             0.717300                           1.133321   
...                                ...                                ...   
1020                          1.241348                           0.417253   
1021                          1.143769                           0.498491   
1022                          1.049673                           1.490560   
1023                          0.687322                           0.033159   
1024                          0.792850                           0.562843   

      Household Income per Capita Country_2  Year_2  \
0                    31051.323158       AUS  2008.0   
1                    30789.699428       AUS  2009.0   
2                    32599.998578       AUS  2010.0   
3                    33941.087440       AUS  2011.0   
4                    36816.129278       AUS  2014.0   
...                           ...       ...     ...   
1020                 19321.329148       EST  2015.0   
1021                 33258.289148       NLD  2016.0   
1022                 40004.983201       USA  2008.0   
1023                          NaN       SVK  1995.0   
1024                          NaN       ISR  2017.0   

      Average Spending on Higher Education (USD/student)  
0                                             15768.220   
1                                             16589.220   
2                                             16300.980   
3                                             16382.440   
4                                             19493.580   
...                                                 ...   
1020                                          12905.990   
1021                                          19873.650   
1022                                          26949.290   
1023                                           4851.865   
1024                                          11423.730   

[1025 rows x 10 columns]

In the table, above there are a lot of missing values. Some countries might not have enrollment rates for either early childhood education or higher education or gdp values, or etc. and because of this a lot of Column values for Country, and Year are filled with Nan. To fix this, we have to make all the values in the Country and Country_2 column the same, and Year and Year_2 values the same. After doing this, we need to drop the Country_2 and Year_2 columns, because they are redundant and change all the float values in Year to be integers.

In [338]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df

Country  Year  GDP per Capita  Total Population  \
0        AUS  2008    40130.341686        21249199.0   
1        AUS  2009    41672.923750        21691653.0   
2        AUS  2010    42816.428960        22031750.0   
3        AUS  2011    44440.579478        22340024.0   
4        AUS  2014    47606.754929        23475686.0   
...      ...   ...             ...               ...   
1020     EST  2015    29222.748082         1314608.0   
1021     NLD  2016    52289.404292        17030314.0   
1022     USA  2008    48498.445211       304093966.0   
1023     SVK  1995     8695.696416         5363676.0   
1024     ISR  2017    39352.294675         8713268.0   

      Public Spending on Education (%)  Private Spending on Education (%)  \
0                             0.689400                           0.844496   
1                             0.734759                           0.882858   
2                             0.778470                           0.896708   
3                             0.743412                           0.885928   
4                             0.717300                           1.133321   
...                                ...                                ...   
1020                          1.241348                           0.417253   
1021                          1.143769                           0.498491   
1022                          1.049673                           1.490560   
1023                          0.687322                           0.033159   
1024                          0.792850                           0.562843   

      Household Income per Capita  \
0                    31051.323158   
1                    30789.699428   
2                    32599.998578   
3                    33941.087440   
4                    36816.129278   
...                           ...   
1020                 19321.329148   
1021                 33258.289148   
1022                 40004.983201   
1023                          NaN   
1024                          NaN   

      Average Spending on Higher Education (USD/student)  
0                                             15768.220   
1                                             16589.220   
2                                             16300.980   
3                                             16382.440   
4                                             19493.580   
...                                                 ...   
1020                                          12905.990   
1021                                          19873.650   
1022                                          26949.290   
1023                                           4851.865   
1024                                          11423.730   

[1025 rows x 8 columns]

## Number of Universities:

We weren't able to find a data set that directly listed the amount of universities in each OECD country. Because of this, we had to make a data set on Excel and convert to a csv later.

All the information from the data set was found from this website: https://www.webometrics.info/en/distribution_by_country


In [339]:
num_universities_df = pd.read_csv('number_of_universities.csv')
num_universities_df

Country  Number of Universities
0      AUS                     187
1      AUT                      84
2      BEL                     142
3      CAN                     383
4      CHL                     130
5      COL                     299
6      CRI                      68
7      CZE                      64
8      DNK                      81
9      EST                      31
10     FIN                      42
11     FRA                     625
12     DEU                     461
13     GRC                      66
14     HUN                      69
15     ISL                       9
16     IRL                      71
17     ISR                      55
18     ITA                     289
19     JPN                     992
20     KOR                     401
21     LVA                      55
22     LTU                      40
23     LUX                       5
24     MEX                    1139
25     NLD                     129
26     NZL                      53
27     NOR                      47
28     POL                     408
29     PRT                     109
30     SVK                      36
31     SVN                      55
32     ESP                     276
33     SWE                      46
34     CHE                     103
35     TUR                     209
36     GBR                     337
37     USA                    3180

The two dataframes (combined_df and num_universities_df) are combined below using a Left Join, so that we will have a cohesive data frame showing enrollment rates, gdp, and total population, public spending as a percentage of GDP, private spending as a percentage of GDP, household income per capita, average spending for higher education per student, and number of universities for each country from 2013-2020.

In [340]:
combined_df = pd.merge(combined_df, num_universities_df, on='Country', how='left')

combined_df

Country  Year  GDP per Capita  Total Population  \
0        AUS  2008    40130.341686        21249199.0   
1        AUS  2009    41672.923750        21691653.0   
2        AUS  2010    42816.428960        22031750.0   
3        AUS  2011    44440.579478        22340024.0   
4        AUS  2014    47606.754929        23475686.0   
...      ...   ...             ...               ...   
1020     EST  2015    29222.748082         1314608.0   
1021     NLD  2016    52289.404292        17030314.0   
1022     USA  2008    48498.445211       304093966.0   
1023     SVK  1995     8695.696416         5363676.0   
1024     ISR  2017    39352.294675         8713268.0   

      Public Spending on Education (%)  Private Spending on Education (%)  \
0                             0.689400                           0.844496   
1                             0.734759                           0.882858   
2                             0.778470                           0.896708   
3                             0.743412                           0.885928   
4                             0.717300                           1.133321   
...                                ...                                ...   
1020                          1.241348                           0.417253   
1021                          1.143769                           0.498491   
1022                          1.049673                           1.490560   
1023                          0.687322                           0.033159   
1024                          0.792850                           0.562843   

      Household Income per Capita  \
0                    31051.323158   
1                    30789.699428   
2                    32599.998578   
3                    33941.087440   
4                    36816.129278   
...                           ...   
1020                 19321.329148   
1021                 33258.289148   
1022                 40004.983201   
1023                          NaN   
1024                          NaN   

      Average Spending on Higher Education (USD/student)  \
0                                             15768.220    
1                                             16589.220    
2                                             16300.980    
3                                             16382.440    
4                                             19493.580    
...                                                 ...    
1020                                          12905.990    
1021                                          19873.650    
1022                                          26949.290    
1023                                           4851.865    
1024                                          11423.730    

      Number of Universities  
0                      187.0  
1                      187.0  
2                      187.0  
3                      187.0  
4                      187.0  
...                      ...  
1020                    31.0  
1021                   129.0  
1022                  3180.0  
1023                    36.0  
1024                    55.0  

[1025 rows x 9 columns]

Since some of the rows above in the combined data frame, have values for OECD, which represents the averages across all the countries, we are going to drop those rows, since not all the data frames that we joined in this value.

In [341]:
combined_df = combined_df[combined_df['Country'] != 'OECD']
combined_df

Country  Year  GDP per Capita  Total Population  \
0        AUS  2008    40130.341686      2.124920e+07   
1        AUS  2009    41672.923750      2.169165e+07   
2        AUS  2010    42816.428960      2.203175e+07   
3        AUS  2011    44440.579478      2.234002e+07   
4        AUS  2014    47606.754929      2.347569e+07   
5        AUS  2015    47226.759745      2.381600e+07   
6        AUS  2016    50136.798381      2.419091e+07   
7        AUS  2019    52785.250556      2.534022e+07   
8        AUT  2016    52665.087457      8.739806e+06   
9        AUT  2017    54188.360666      8.795073e+06   
10       AUT  2018    56956.110562      8.837707e+06   
11       AUT  2019    59716.251399      8.877637e+06   
12       BEL  2008    37883.233422      1.070911e+07   
13       BEL  2011    40943.343479      1.099361e+07   
14       BEL  2013    43672.712292      1.112503e+07   
15       BEL  2014    44929.933328      1.117978e+07   
16       BEL  2016    48599.202676      1.129500e+07   
17       BEL  2017    50442.947518      1.134908e+07   
18       BEL  2019    55804.713631      1.146202e+07   
19       BEL  2020    54544.419240      1.150694e+07   
20       CAN  2015    44670.054374      3.570291e+07   
21       CAN  2016    46472.368771      3.610949e+07   
22       CAN  2017    48317.191163      3.654524e+07   
23       CAN  2018    49992.811418      3.706508e+07   
24       CAN  2019    49832.414539      3.760123e+07   
25       CZE  2008    27853.549898      1.042969e+07   
26       CZE  2010    27766.983552      1.051725e+07   
27       CZE  2013    30828.526409      1.051072e+07   
28       CZE  2015    33909.309243      1.054294e+07   
29       CZE  2016    36101.285601      1.056528e+07   
30       CZE  2017    38842.896268      1.058953e+07   
31       CZE  2019    44223.295751      1.066932e+07   
32       CZE  2020    42817.867499      1.070016e+07   
33       DNK  2008    41282.995471      5.489022e+06   
34       DNK  2009    40332.516629      5.519441e+06   
35       DNK  2011    44407.942070      5.566856e+06   
36       DNK  2014    47905.477079      5.639719e+06   
37       DNK  2016    51967.020438      5.724456e+06   
38       DNK  2018    57479.350221      5.789957e+06   
39       DNK  2019    59884.117380      5.814461e+06   
40       DNK  2020    60768.060489      5.825337e+06   
41       FIN  2008    40083.701943      5.313398e+06   
42       FIN  2009    37972.457701      5.338867e+06   
43       FIN  2010    38954.131777      5.363341e+06   
44       FIN  2011    40916.647325      5.388272e+06   
45       FIN  2013    41492.918416      5.438975e+06   
46       FIN  2016    44934.488245      5.495297e+06   
47       FIN  2018    49573.255773      5.515525e+06   
48       FIN  2020    52294.342491      5.529545e+06   
49       FRA  2008    35102.870428      6.413317e+07   
50       FRA  2009    34686.479663      6.445872e+07   
51       FRA  2010    35910.195851      6.477317e+07   
52       FRA  2014    40144.059485      6.627667e+07   
53       FRA  2015    40829.893311      6.651256e+07   
54       FRA  2016    42855.944562      6.668856e+07   
55       FRA  2017    44444.934559      6.688331e+07   
56       FRA  2018    46336.933985      6.712507e+07   
57       FRA  2019    50226.680167      6.734992e+07   
58       FRA  2020    47982.359606      6.753848e+07   
59       DEU  2010    39675.002380      8.177694e+07   
60       DEU  2014    47011.280402      8.098250e+07   
61       DEU  2015    47609.557159      8.168661e+07   
62       DEU  2016    50579.483717      8.234867e+07   
63       DEU  2020    56454.181109      8.316088e+07   
64       GRC  2013    25986.640698      1.096521e+07   
65       GRC  2014    26625.159298      1.089242e+07   
66       GRC  2015    26760.280798      1.082088e+07   
67       GRC  2017    28604.829152      1.075468e+07   
68       GRC  2018    29617.518625      1.073288e+07   
69       GRC  2019    31155.946796      1.072158e+07   
70       HUN  2016    27941.9

In [342]:
combined_df.to_csv('combined_data.csv', index=False)

## Students per Teaching Staff:

https://data.oecd.org/teachers/students-per-teaching-staff.htm

In [343]:
students_per_teacher_df = pd.read_csv('students_per_teaching_staff.csv')

In [344]:
students_per_teacher_df.head()

LOCATION       INDICATOR        SUBJECT MEASURE FREQUENCY  TIME   Value  \
0      AUT  STUDPERTEACHER  EARLYCHILDEDU      RT         A  2013  12.798   
1      AUT  STUDPERTEACHER  EARLYCHILDEDU      RT         A  2014  12.926   
2      AUT  STUDPERTEACHER  EARLYCHILDEDU      RT         A  2015  12.537   
3      AUT  STUDPERTEACHER  EARLYCHILDEDU      RT         A  2016  12.346   
4      AUT  STUDPERTEACHER  EARLYCHILDEDU      RT         A  2017  12.709   

   Flag Codes  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN

In [345]:
query = """
        SELECT 
            LOCATION AS Country,
            TIME AS Year,
            Value AS "Students per Teaching Staff"
        FROM students_per_teacher_df
        WHERE TIME IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
students_per_teacher_df = duckdb.sql(query).df()
students_per_teacher_df

Country  Year  Students per Teaching Staff
0       AUT  2013                       12.798
1       AUT  2014                       12.926
2       AUT  2015                       12.537
3       AUT  2016                       12.346
4       AUT  2017                       12.709
5       AUT  2018                       12.541
6       AUT  2019                       11.999
7       AUT  2020                       12.125
8       CZE  2013                       13.891
9       CZE  2014                       13.666
10      CZE  2015                       13.455
11      CZE  2016                       13.403
12      CZE  2017                       13.168
13      CZE  2018                       13.070
14      CZE  2019                       12.970
15      CZE  2020                       12.283
16      DNK  2014                       10.384
17      DNK  2018                        7.704
18      DNK  2019                        7.472
19      DNK  2020                        7.515
20      FRA  2013                       24.181
21      FRA  2014                       24.116
22      FRA  2015                       24.113
23      FRA  2016                       23.931
24      FRA  2017                       23.638
25      FRA  2018                       23.458
26      FRA  2019                       23.290
27      FRA  2020                       23.155
28      DEU  2013                        8.335
29      DEU  2014                        8.054
30      DEU  2015                        7.830
31      DEU  2016                        7.761
32      DEU  2017                        7.617
33      DEU  2018                        7.479
34      DEU  2019                        7.446
35      DEU  2020                        7.365
36      HUN  2015                       12.438
37      HUN  2016                       12.328
38      HUN  2017                       12.234
39      HUN  2018                       12.420
40      HUN  2019                       12.691
41      HUN  2020                       13.011
42      ISL  2013                        4.699
43      ISL  2014                        4.608
44      ISL  2015                        4.479
45      ISL  2016                        4.347
46      ISL  2017                        4.346
47      ISL  2018                        4.208
48      ISL  2019                        4.053
49      ISL  2020                        3.860
50      IRL  2018                        4.210
51      IRL  2019                        3.962
52      IRL  2020                        3.973
53      ITA  2015                       13.198
54      ITA  2016                       12.856
55      ITA  2017                       12.435
56      ITA  2018                       12.208
57      ITA  2019                       11.961
58      ITA  2020                       11.815
59      JPN  2013                       15.408
60      JPN  2014                       15.111
61      JPN  2015                       14.791
62      JPN  2016                       14.556
63      JPN  2017                       14.515
64      JPN  2018                       14.044
65      JPN  2019                       13.614
66      JPN  2020                       13.214
67      KOR  2013                        8.920
68      KOR  2014                        8.752
69      KOR  2015                        8.679
70      KOR  2016                        8.633
71      KOR  2017                        8.597
72      KOR  2018                        8.481
73      KOR  2019                        8.419
74      KOR  2020                        8.319
75      LUX  2013                       10.855
76      LUX  2014                       11.112
77      LUX  2015                       10.797
78      LUX  2016                       11.464
79      LUX  2017                       14.470
80      LUX  2018                       12.110
81      LUX  2019                       11.800
82      LUX  2020                        8.509
83      MEX  2013                       26.059
84      M

In [346]:
students_per_teacher_df.to_csv('clean_students_per_teacher_df.csv', index=False)

In [347]:
query = """
        SELECT *
        FROM combined_df
        FULL JOIN students_per_teacher_df
        ON combined_df.Country = students_per_teacher_df.Country
        AND combined_df.Year = students_per_teacher_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df 

Country  Year  GDP per Capita  Total Population  \
0       AUT  2016    52665.087457      8.739806e+06   
1       AUT  2017    54188.360666      8.795073e+06   
2       AUT  2018    56956.110562      8.837707e+06   
3       AUT  2019    59716.251399      8.877637e+06   
4       CZE  2013    30828.526409      1.051072e+07   
5       CZE  2015    33909.309243      1.054294e+07   
6       CZE  2016    36101.285601      1.056528e+07   
7       CZE  2017    38842.896268      1.058953e+07   
8       CZE  2019    44223.295751      1.066932e+07   
9       CZE  2020    42817.867499      1.070016e+07   
10      DNK  2014    47905.477079      5.639719e+06   
11      DNK  2018    57479.350221      5.789957e+06   
12      DNK  2019    59884.117380      5.814461e+06   
13      DNK  2020    60768.060489      5.825337e+06   
14      FRA  2014    40144.059485      6.627667e+07   
15      FRA  2015    40829.893311      6.651256e+07   
16      FRA  2016    42855.944562      6.668856e+07   
17      FRA  2017    44444.934559      6.688331e+07   
18      FRA  2018    46336.933985      6.712507e+07   
19      FRA  2019    50226.680167      6.734992e+07   
20      FRA  2020    47982.359606      6.753848e+07   
21      DEU  2014    47011.280402      8.098250e+07   
22      DEU  2015    47609.557159      8.168661e+07   
23      DEU  2016    50579.483717      8.234867e+07   
24      DEU  2020    56454.181109      8.316088e+07   
25      HUN  2016    27941.926751      9.814026e+06   
26      HUN  2017    29496.163748      9.787969e+06   
27      HUN  2018    31908.863431      9.775566e+06   
28      HUN  2020    34169.922355      9.750153e+06   
29      IRL  2018    85034.728547      4.857015e+06   
30      IRL  2019    89759.238887      4.921496e+06   
31      IRL  2020    94646.640757      4.977443e+06   
32      ITA  2015    37206.331822      6.022960e+07   
33      ITA  2016    40267.222623      6.011522e+07   
34      ITA  2017    41951.466331      6.000225e+07   
35      ITA  2018    43427.663143      5.987722e+07   
36      ITA  2019    45799.741922      5.972908e+07   
37      ITA  2020    43150.115981      5.943884e+07   
38      JPN  2014    39559.763471      1.272372e+08   
39      JPN  2015    40908.781547      1.270947e+08   
40      JPN  2016    40642.704531      1.270418e+08   
41      JPN  2018    42264.585123      1.267485e+08   
42      JPN  2020    41867.153393      1.261461e+08   
43      KOR  2016    39575.302078      5.121780e+07   
44      KOR  2018    43044.340145      5.158506e+07   
45      KOR  2019    43410.152957      5.176482e+07   
46      KOR  2020    44694.939796      5.183624e+07   
47      LUX  2014   104917.945675      5.563220e+05   
48      LUX  2015   107898.304236      5.696050e+05   
49      LUX  2016   112955.470175      5.834590e+05   
50      LUX  2017   114862.528755      5.963370e+05   
51      LUX  2019   119364.151427      6.200030e+05   
52      LUX  2020   119407.898814      6.304130e+05   
53      MEX  2013    17437.042083      1.184539e+08   
54      MEX  2014    18153.351036      1.199364e+08   
55      MEX  2016    19791.259772      1.227152e+08   
56      MEX  2018    20561.246895      1.253278e+08   
57      MEX  2019    20244.557477      1.265777e+08   
58      NLD  2013    49242.786711      1.680443e+07   
59      NLD  2014    49233.230349      1.686501e+07   
60      NLD  2015    50288.352815      1.693992e+07   
61      NLD  2017    55089.581430      1.713130e+07   
62      NLD  2018    57825.399708      1.723162e+07   
63      NZL  2015    37246.951138      4.609400e+06   
64      NZL  2016    39696.946073      4.714100e+06   
65      NZL  2018    42320.906448      4.900600e+06   
66      NOR  2013    67372.928181      5.080171e+06   
67      NOR  2014    66335.459647      5.137427e+06   
68      NOR  2015    60721.583813      5.189898e+06   
69      NOR  2017    64589.163172      5.276965e+06   
70      NOR  2018    70252.735449      5.311916e+06   
71      NOR  2019    69915.017660      5.347

In [348]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df

Country  Year  GDP per Capita  Total Population  \
0       AUT  2016    52665.087457      8.739806e+06   
1       AUT  2017    54188.360666      8.795073e+06   
2       AUT  2018    56956.110562      8.837707e+06   
3       AUT  2019    59716.251399      8.877637e+06   
4       CZE  2013    30828.526409      1.051072e+07   
5       CZE  2015    33909.309243      1.054294e+07   
6       CZE  2016    36101.285601      1.056528e+07   
7       CZE  2017    38842.896268      1.058953e+07   
8       CZE  2019    44223.295751      1.066932e+07   
9       CZE  2020    42817.867499      1.070016e+07   
10      DNK  2014    47905.477079      5.639719e+06   
11      DNK  2018    57479.350221      5.789957e+06   
12      DNK  2019    59884.117380      5.814461e+06   
13      DNK  2020    60768.060489      5.825337e+06   
14      FRA  2014    40144.059485      6.627667e+07   
15      FRA  2015    40829.893311      6.651256e+07   
16      FRA  2016    42855.944562      6.668856e+07   
17      FRA  2017    44444.934559      6.688331e+07   
18      FRA  2018    46336.933985      6.712507e+07   
19      FRA  2019    50226.680167      6.734992e+07   
20      FRA  2020    47982.359606      6.753848e+07   
21      DEU  2014    47011.280402      8.098250e+07   
22      DEU  2015    47609.557159      8.168661e+07   
23      DEU  2016    50579.483717      8.234867e+07   
24      DEU  2020    56454.181109      8.316088e+07   
25      HUN  2016    27941.926751      9.814026e+06   
26      HUN  2017    29496.163748      9.787969e+06   
27      HUN  2018    31908.863431      9.775566e+06   
28      HUN  2020    34169.922355      9.750153e+06   
29      IRL  2018    85034.728547      4.857015e+06   
30      IRL  2019    89759.238887      4.921496e+06   
31      IRL  2020    94646.640757      4.977443e+06   
32      ITA  2015    37206.331822      6.022960e+07   
33      ITA  2016    40267.222623      6.011522e+07   
34      ITA  2017    41951.466331      6.000225e+07   
35      ITA  2018    43427.663143      5.987722e+07   
36      ITA  2019    45799.741922      5.972908e+07   
37      ITA  2020    43150.115981      5.943884e+07   
38      JPN  2014    39559.763471      1.272372e+08   
39      JPN  2015    40908.781547      1.270947e+08   
40      JPN  2016    40642.704531      1.270418e+08   
41      JPN  2018    42264.585123      1.267485e+08   
42      JPN  2020    41867.153393      1.261461e+08   
43      KOR  2016    39575.302078      5.121780e+07   
44      KOR  2018    43044.340145      5.158506e+07   
45      KOR  2019    43410.152957      5.176482e+07   
46      KOR  2020    44694.939796      5.183624e+07   
47      LUX  2014   104917.945675      5.563220e+05   
48      LUX  2015   107898.304236      5.696050e+05   
49      LUX  2016   112955.470175      5.834590e+05   
50      LUX  2017   114862.528755      5.963370e+05   
51      LUX  2019   119364.151427      6.200030e+05   
52      LUX  2020   119407.898814      6.304130e+05   
53      MEX  2013    17437.042083      1.184539e+08   
54      MEX  2014    18153.351036      1.199364e+08   
55      MEX  2016    19791.259772      1.227152e+08   
56      MEX  2018    20561.246895      1.253278e+08   
57      MEX  2019    20244.557477      1.265777e+08   
58      NLD  2013    49242.786711      1.680443e+07   
59      NLD  2014    49233.230349      1.686501e+07   
60      NLD  2015    50288.352815      1.693992e+07   
61      NLD  2017    55089.581430      1.713130e+07   
62      NLD  2018    57825.399708      1.723162e+07   
63      NZL  2015    37246.951138      4.609400e+06   
64      NZL  2016    39696.946073      4.714100e+06   
65      NZL  2018    42320.906448      4.900600e+06   
66      NOR  2013    67372.928181      5.080171e+06   
67      NOR  2014    66335.459647      5.137427e+06   
68      NOR  2015    60721.583813      5.189898e+06   
69      NOR  2017    64589.163172      5.276965e+06   
70      NOR  2018    70252.735449      5.311916e+06   
71      NOR  2019    69915.017660      5.347

## Education Enrollment and Completion Rates:

https://ourworldindata.org/grapher/primary-secondary-enrollment-completion-rates?tab=table

In [349]:
enrollment_rates_df = pd.read_csv('enrollment_completion_rates.csv')

In [350]:
enrollment_rates_df.head()

Entity Code  Year  \
0  Afghanistan  AFG  1974   
1  Afghanistan  AFG  1977   
2  Afghanistan  AFG  1978   
3  Afghanistan  AFG  1980   
4  Afghanistan  AFG  1981   

   Primary completion rate, total (% of relevant age group)  \
0                                           16.65700          
1                                           17.88076          
2                                           19.65284          
3                                           26.37324          
4                                           32.70612          

   Completion rate, upper secondary education, both sexes (%)  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                                NaN            
4                                                NaN            

   Completion rate, lower secondary education, both sexes (%)  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                                NaN            
4                                                NaN            

   School enrollment, primary (% gross)  \
0                              33.10830   
1                              36.11149   
2                              37.63702   
3                              44.13337   
4                              47.71170   

   School enrollment, secondary (% gross)  \
0                                10.91069   
1                                13.13156   
2                                13.82176   
3                                16.76427   
4                                19.32814   

   School enrollment, tertiary (% gross)  
0                                1.02260  
1                                1.40822  
2                                1.80833  
3                                    NaN  
4                                    NaN

In [351]:
oecd_list = ["AUS","AUT","BEL", "CAN", "CHL", "COL", "CRI",
            "CZE", "DNK", "EST", "FIN", "FRA", "DEU", "GRC", 
             "HUN", "ISL", "IRL", "ISR", "ITA", "JPN", "KOR", 
            "LVA", "LTU", "LUX", "MEX", "NLD", "NZL",
            "NOR", "POL", "PRT", "SVK","SVN","ESP","SWE",
            "CHE", "TUR","GBR","USA"]

In [352]:
enrollment_rates_df = enrollment_rates_df.loc[enrollment_rates_df['Code'].isin(oecd_list)]

In [353]:
enrollment_rates_df

Entity Code  Year  \
379       Australia  AUS  2010   
380       Australia  AUS  1971   
381       Australia  AUS  1972   
382       Australia  AUS  1973   
383       Australia  AUS  1974   
...             ...  ...   ...   
8963  United States  USA  2014   
8964  United States  USA  2020   
8965  United States  USA  1988   
8966  United States  USA  1989   
8967  United States  USA  1992   

      Primary completion rate, total (% of relevant age group)  \
379                                                 NaN          
380                                                 NaN          
381                                                 NaN          
382                                                 NaN          
383                                                 NaN          
...                                                 ...          
8963                                                NaN          
8964                                                NaN          
8965                                                NaN          
8966                                                NaN          
8967                                                NaN          

      Completion rate, upper secondary education, both sexes (%)  \
379                                               85.02            
380                                                 NaN            
381                                                 NaN            
382                                                 NaN            
383                                                 NaN            
...                                                 ...            
8963                                                NaN            
8964                                                NaN            
8965                                                NaN            
8966                                                NaN            
8967                                                NaN            

      Completion rate, lower secondary education, both sexes (%)  \
379                                               99.15            
380                                                 NaN            
381                                                 NaN            
382                                                 NaN            
383                                                 NaN            
...                                                 ...            
8963                                                NaN            
8964                                                NaN            
8965                                                NaN            
8966                                                NaN            
8967                                                NaN            

      School enrollment, primary (% gross)  \
379                              105.61943   
380                              111.19781   
381                              110.64366   
382                              110.00005   
383                              105.23748   
...                                    ...   
8963                              99.67338   
8964                             100.30579   
8965                                   NaN   
8966                                   NaN   
8967                                   NaN   

      School enrollment, secondary (% gross)  \
379                                      NaN   
380                                      NaN   
381                                      NaN   
382                                      NaN   
383                                      NaN   
...                                      ...   
8963                                96.92454   
8964                               100.50982   
8965                                     NaN   
8966                                     NaN   
8967                                     NaN   

      School enrollment, tertiary (% gross)  
3

In [354]:
query = """
        SELECT
            Code AS Country,
            Year,
            "Primary completion rate, total (% of relevant age group)" AS "Primary Completion Rate (%)",
            "Completion rate, upper secondary education, both sexes (%)" AS "Upper Secondary Completion Rate (%)",
            "Completion rate, lower secondary education, both sexes (%)" AS "Lower Secondary Completion Rate (%)",
            "School enrollment, primary (% gross)" AS "Primary Enrollment rate (% gross)",
            "School enrollment, secondary (% gross)" AS "Secondary Enrollment rate (% gross)",
            "School enrollment, tertiary (% gross)" AS "Tertiary Enrollment rate (% gross)"
        FROM enrollment_rates_df
        WHERE Year IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """

enrollment_rates_df = duckdb.sql(query).df()

In [355]:
enrollment_rates_df.head()

Country  Year  Primary Completion Rate (%)  \
0     AUS  2010                          NaN   
1     AUS  1995                          NaN   
2     AUS  1996                          NaN   
3     AUS  1997                          NaN   
4     AUS  1998                          NaN   

   Upper Secondary Completion Rate (%)  Lower Secondary Completion Rate (%)  \
0                                85.02                                99.15   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                  NaN                                  NaN   

   Primary Enrollment rate (% gross)  Secondary Enrollment rate (% gross)  \
0                          105.61943                                  NaN   
1                          101.29127                            143.23387   
2                          101.58029                            148.63600   
3                          101.18403                            152.93597   
4                          100.92862                                  NaN   

   Tertiary Enrollment rate (% gross)  
0                                 NaN  
1                            70.68857  
2                            75.64778  
3                            80.90665  
4                                 NaN

In [356]:
enrollment_rates_df.to_csv('clean_enrollment_rates__1_df.csv', index=False)

In [357]:
query = """
        SELECT *
        FROM combined_df
        FULL JOIN enrollment_rates_df
        ON combined_df.Country = enrollment_rates_df.Country
        AND combined_df.Year = enrollment_rates_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df.head()

Country  Year  GDP per Capita  Total Population  \
0     AUT  2016    52665.087457         8739806.0   
1     AUT  2017    54188.360666         8795073.0   
2     AUT  2018    56956.110562         8837707.0   
3     AUT  2019    59716.251399         8877637.0   
4     CZE  2013    30828.526409        10510719.0   

   Public Spending on Education (%)  Private Spending on Education (%)  \
0                          1.631474                           0.112024   
1                          1.560725                           0.152499   
2                          1.552325                           0.182909   
3                          1.557053                           0.192745   
4                          0.851949                           0.254183   

   Household Income per Capita  \
0                 36227.955632   
1                 36984.312014   
2                 38190.870562   
3                 40065.855276   
4                 20841.747191   

   Average Spending on Higher Education (USD/student)  Number of Universities  \
0                                           18625.00                     84.0   
1                                           18974.75                     84.0   
2                                           20416.62                     84.0   
3                                           21946.23                     84.0   
4                                           10307.66                     64.0   

   Students per Teaching Staff Country_2  Year_2  Primary Completion Rate (%)  \
0                       12.346       AUT  2016.0                     99.65672   
1                       12.709       AUT  2017.0                     99.45318   
2                       12.541       AUT  2018.0                     99.81300   
3                       11.999       AUT  2019.0                     99.40850   
4                       13.891       CZE  2013.0                     99.76104   

   Upper Secondary Completion Rate (%)  Lower Secondary Completion Rate (%)  \
0                                  NaN                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                92.68                                99.37   

   Primary Enrollment rate (% gross)  Secondary Enrollment rate (% gross)  \
0                          102.26436                            100.96302   
1                          103.11315                            100.45521   
2                          103.31685                             99.95784   
3                          103.10493                            100.19370   
4                           98.74181                            103.99895   

   Tertiary Enrollment rate (% gross)  
0                            83.45495  
1                            85.05714  
2                            86.68835  
3                            86.47553  
4                            65.08577

In [358]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df.head()

Country  Year  GDP per Capita  Total Population  \
0     AUT  2016    52665.087457         8739806.0   
1     AUT  2017    54188.360666         8795073.0   
2     AUT  2018    56956.110562         8837707.0   
3     AUT  2019    59716.251399         8877637.0   
4     CZE  2013    30828.526409        10510719.0   

   Public Spending on Education (%)  Private Spending on Education (%)  \
0                          1.631474                           0.112024   
1                          1.560725                           0.152499   
2                          1.552325                           0.182909   
3                          1.557053                           0.192745   
4                          0.851949                           0.254183   

   Household Income per Capita  \
0                 36227.955632   
1                 36984.312014   
2                 38190.870562   
3                 40065.855276   
4                 20841.747191   

   Average Spending on Higher Education (USD/student)  Number of Universities  \
0                                           18625.00                     84.0   
1                                           18974.75                     84.0   
2                                           20416.62                     84.0   
3                                           21946.23                     84.0   
4                                           10307.66                     64.0   

   Students per Teaching Staff  Primary Completion Rate (%)  \
0                       12.346                     99.65672   
1                       12.709                     99.45318   
2                       12.541                     99.81300   
3                       11.999                     99.40850   
4                       13.891                     99.76104   

   Upper Secondary Completion Rate (%)  Lower Secondary Completion Rate (%)  \
0                                  NaN                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                92.68                                99.37   

   Primary Enrollment rate (% gross)  Secondary Enrollment rate (% gross)  \
0                          102.26436                            100.96302   
1                          103.11315                            100.45521   
2                          103.31685                             99.95784   
3                          103.10493                            100.19370   
4                           98.74181                            103.99895   

   Tertiary Enrollment rate (% gross)  
0                            83.45495  
1                            85.05714  
2                            86.68835  
3                            86.47553  
4                            65.08577

In [359]:
query = """
        SELECT *
        FROM combined_df
        ORDER BY Country, Year
        """
combined_df = duckdb.sql(query).df()

In [360]:
combined_df

Country  Year  GDP per Capita  Total Population  \
0       AUS  1995    22442.316842      1.800488e+07   
1       AUS  1996    23289.401829      1.822477e+07   
2       AUS  1997    24477.413795      1.842304e+07   
3       AUS  1998    25708.263828      1.860758e+07   
4       AUS  1999    27139.248201      1.881226e+07   
5       AUS  2000    28312.859441      1.902880e+07   
6       AUS  2001    29546.415014      1.927470e+07   
7       AUS  2002    30807.514079      1.949521e+07   
8       AUS  2003    32391.486238      1.972074e+07   
9       AUS  2004    34000.173773      1.993272e+07   
10      AUS  2005    35659.125487      2.017684e+07   
11      AUS  2006    37938.792079      2.045097e+07   
12      AUS  2007    39687.448610      2.082762e+07   
13      AUS  2008    40130.341686      2.124920e+07   
14      AUS  2009    41672.923750      2.169165e+07   
15      AUS  2010    42816.428960      2.203175e+07   
16      AUS  2011    44440.579478      2.234002e+07   
17      AUS  2012    43884.635595      2.273346e+07   
18      AUS  2013    47763.215900      2.312813e+07   
19      AUS  2014    47606.754929      2.347569e+07   
20      AUS  2015    47226.759745      2.381600e+07   
21      AUS  2016    50136.798381      2.419091e+07   
22      AUS  2017    50706.489861      2.459420e+07   
23      AUS  2018    53025.386896      2.496664e+07   
24      AUS  2019    52785.250556      2.534022e+07   
25      AUS  2020    55772.741079      2.565529e+07   
26      AUT  1995    23698.103090      7.948278e+06   
27      AUT  1996    24560.615338      7.959016e+06   
28      AUT  1997    25426.661912      7.968041e+06   
29      AUT  1998    26675.649686      7.976789e+06   
30      AUT  1999    27606.484243      7.992323e+06   
31      AUT  2000    29381.672832      8.011566e+06   
32      AUT  2001    29708.489450      8.042293e+06   
33      AUT  2002    31178.051444      8.082121e+06   
34      AUT  2003    32158.459529      8.118245e+06   
35      AUT  2004    33784.446804      8.169441e+06   
36      AUT  2005    35024.557484      8.225278e+06   
37      AUT  2006    37662.888035      8.267948e+06   
38      AUT  2007    39437.038795      8.295189e+06   
39      AUT  2008    41316.022642      8.321541e+06   
40      AUT  2009    40927.556365      8.341483e+06   
41      AUT  2010    42019.005887      8.361069e+06   
42      AUT  2011    44469.209642      8.388534e+06   
43      AUT  2012    46477.655075      8.426311e+06   
44      AUT  2013    47936.677963      8.477230e+06   
45      AUT  2014    48813.534409      8.543932e+06   
46      AUT  2015    49942.056293      8.629519e+06   
47      AUT  2016    52665.087457      8.739806e+06   
48      AUT  2017    54188.360666      8.795073e+06   
49      AUT  2018    56956.110562      8.837707e+06   
50      AUT  2019    59716.251399      8.877637e+06   
51      AUT  2020    57235.673886      8.916845e+06   
52      BEL  1995    22447.051902      1.013681e+07   
53      BEL  1996    22743.894711      1.015664e+07   
54      BEL  1997    23732.789845      1.018125e+07   
55      BEL  1998    24369.501242      1.020301e+07   
56      BEL  1999    25441.891387      1.022642e+07   
57      BEL  2000    27790.606306      1.025125e+07   
58      BEL  2001    28792.401342      1.028657e+07   
59      BEL  2002    30281.667989      1.033279e+07   
60      BEL  2003    30934.823303      1.037613e+07   
61      BEL  2004    32063.687224      1.042114e+07   
62      BEL  2005    33176.680884      1.047862e+07   
63      BEL  2006    35256.775979      1.054796e+07   
64      BEL  2007    36794.811405      1.062484e+07   
65      BEL  2008    37883.233422      1.070911e+07   
66      BEL  2009    37751.634063      1.079650e+07   
67      BEL  2010    39836.533412      1.089559e+07   
68      BEL  2011    40943.343479      1.099361e+07   
69      BEL  2012    42290.477674      1.106775e+07   
70      BEL  2013    43672.712292      1.112503e+07   
71      BEL  2014    44929.933328      1.117

https://data.worldbank.org/indicator/SE.XPD.TOTL.GD.ZS?view=chart

In [361]:
government_expenditure_df = pd.read_csv('total-government-expenditure-on-education-gdp.csv')

In [362]:
government_expenditure_df.head()

Entity Code  Year  Historical and more recent expenditure estimates
0  Afghanistan  AFG  1971                                           1.16036
1  Afghanistan  AFG  1972                                           1.11718
2  Afghanistan  AFG  1973                                           1.42788
3  Afghanistan  AFG  1975                                           1.30332
4  Afghanistan  AFG  1979                                           1.73981

In [363]:
query = """
        SELECT 
            Code AS Country,
            Year,
            "Historical and more recent expenditure estimates" AS "Government Expenditure On Education (%)"
        FROM government_expenditure_df
        WHERE Year IN (1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020);
        """
government_expenditure_df = duckdb.sql(query).df()
government_expenditure_df

Country  Year  Government Expenditure On Education (%)
0        AFG  2005                                  2.57000
1        AFG  2006                                  2.90000
2        AFG  2007                                  2.85000
3        AFG  2008                                  3.51000
4        AFG  2009                                  3.73000
...      ...   ...                                      ...
3744     ZWE  2014                                  6.13835
3745     ZWE  2015                                  5.81279
3746     ZWE  2016                                  5.47262
3747     ZWE  2017                                  5.81878
3748     ZWE  2018                                  3.86611

[3749 rows x 3 columns]

In [364]:
government_expenditure_df = government_expenditure_df.loc[government_expenditure_df['Country'].isin(oecd_list)]

In [365]:
government_expenditure_df

Country  Year  Government Expenditure On Education (%)
180      AUS  1995                                 5.134130
181      AUS  1996                                 5.231000
182      AUS  2000                                 4.887310
183      AUS  2005                                 4.898520
184      AUS  2006                                 4.740650
185      AUS  2007                                 4.656220
186      AUS  2008                                 4.632780
187      AUS  2009                                 5.084520
188      AUS  2010                                 5.543040
189      AUS  2011                                 5.069950
190      AUS  2012                                 4.867880
191      AUS  2013                                 5.229240
192      AUS  2014                                 5.164690
193      AUS  2015                                 5.315840
194      AUS  2016                                 5.286230
195      AUS  2017                                 5.136810
196      AUS  2018                                 5.123450
197      AUS  2019                                 5.135310
198      AUS  2020                                 6.100000
199      AUT  1995                                 5.428350
200      AUT  1996                                 5.259900
201      AUT  1998                                 6.103740
202      AUT  1999                                 6.112340
203      AUT  2000                                 5.588810
204      AUT  2001                                 5.575480
205      AUT  2002                                 5.522130
206      AUT  2003                                 5.361830
207      AUT  2004                                 5.302430
208      AUT  2005                                 5.249370
209      AUT  2006                                 5.226520
210      AUT  2007                                 5.146900
211      AUT  2008                                 5.263960
212      AUT  2009                                 5.730250
213      AUT  2010                                 5.700480
214      AUT  2011                                 5.592270
215      AUT  2012                                 5.480400
216      AUT  2013                                 5.547110
217      AUT  2014                                 5.447620
218      AUT  2015                                 5.456580
219      AUT  2016                                 5.479620
220      AUT  2017                                 5.371590
221      AUT  2018                                 5.224520
222      AUT  2019                                 5.212910
223      AUT  2020                                 5.070000
340      BEL  1995                                 2.988660
341      BEL  1996                                 3.049480
342      BEL  2005                                 5.795860
343      BEL  2008                                 6.332940
344      BEL  2009                                 6.458100
345      BEL  2010                                 6.442590
346      BEL  2011                                 6.431990
347      BEL  2012                                 6.255765
348      BEL  2013                                 6.630530
349      BEL  2014                                 6.590470
350      BEL  2015                                 6.451570
351      BEL  2016                                 6.461730
352      BEL  2017                                 6.425340
353      BEL  2018                                 6.381370
354      BEL  2019                                 6.339760
355      BEL  2020                                 6.710000
586      CAN  1995                                 6.324450
587      CAN  1998                                 5.493770
588      CAN  1999                                 5.530800
589      CAN  2000                                 5.423320
590      CAN  2001                                 4.953030
591      CAN  2002                           

In [366]:
query = """
        SELECT *
        FROM combined_df
        FULL JOIN government_expenditure_df
        ON combined_df.Country = government_expenditure_df.Country
        AND combined_df.Year = government_expenditure_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df.head()

Country  Year  GDP per Capita  Total Population  \
0     AUS  1995    22442.316842        18004882.0   
1     AUS  1996    23289.401829        18224767.0   
2     AUS  2000    28312.859441        19028802.0   
3     AUS  2005    35659.125487        20176844.0   
4     AUS  2006    37938.792079        20450966.0   

   Public Spending on Education (%)  Private Spending on Education (%)  \
0                               NaN                                NaN   
1                               NaN                                NaN   
2                          0.744540                           0.748428   
3                          0.689385                           0.828712   
4                               NaN                                NaN   

   Household Income per Capita  \
0                          NaN   
1                          NaN   
2                          NaN   
3                          NaN   
4                          NaN   

   Average Spending on Higher Education (USD/student)  Number of Universities  \
0                                                NaN                    187.0   
1                                                NaN                    187.0   
2                                           12500.20                    187.0   
3                                           14171.66                    187.0   
4                                                NaN                    187.0   

   Students per Teaching Staff  Primary Completion Rate (%)  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                          NaN   
4                          NaN                          NaN   

   Upper Secondary Completion Rate (%)  Lower Secondary Completion Rate (%)  \
0                                  NaN                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                  NaN                                  NaN   

   Primary Enrollment rate (% gross)  Secondary Enrollment rate (% gross)  \
0                          101.29127                            143.23387   
1                          101.58029                            148.63600   
2                          100.72193                                  NaN   
3                          102.73932                                  NaN   
4                          103.30405                                  NaN   

   Tertiary Enrollment rate (% gross) Country_2  Year_2  \
0                            70.68857       AUS  1995.0   
1                            75.64778       AUS  1996.0   
2                                 NaN       AUS  2000.0   
3                                 NaN       AUS  2005.0   
4                                 NaN       AUS  2006.0   

   Government Expenditure On Education (%)  
0                                  5.13413  
1                                  5.23100  
2                                  4.88731  
3                                  4.89852  
4                                  4.74065

In [367]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df.head()

Country  Year  GDP per Capita  Total Population  \
0     AUS  1995    22442.316842        18004882.0   
1     AUS  1996    23289.401829        18224767.0   
2     AUS  2000    28312.859441        19028802.0   
3     AUS  2005    35659.125487        20176844.0   
4     AUS  2006    37938.792079        20450966.0   

   Public Spending on Education (%)  Private Spending on Education (%)  \
0                               NaN                                NaN   
1                               NaN                                NaN   
2                          0.744540                           0.748428   
3                          0.689385                           0.828712   
4                               NaN                                NaN   

   Household Income per Capita  \
0                          NaN   
1                          NaN   
2                          NaN   
3                          NaN   
4                          NaN   

   Average Spending on Higher Education (USD/student)  Number of Universities  \
0                                                NaN                    187.0   
1                                                NaN                    187.0   
2                                           12500.20                    187.0   
3                                           14171.66                    187.0   
4                                                NaN                    187.0   

   Students per Teaching Staff  Primary Completion Rate (%)  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                          NaN   
4                          NaN                          NaN   

   Upper Secondary Completion Rate (%)  Lower Secondary Completion Rate (%)  \
0                                  NaN                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                  NaN                                  NaN   

   Primary Enrollment rate (% gross)  Secondary Enrollment rate (% gross)  \
0                          101.29127                            143.23387   
1                          101.58029                            148.63600   
2                          100.72193                                  NaN   
3                          102.73932                                  NaN   
4                          103.30405                                  NaN   

   Tertiary Enrollment rate (% gross)  Government Expenditure On Education (%)  
0                            70.68857                                  5.13413  
1                            75.64778                                  5.23100  
2                                 NaN                                  4.88731  
3                                 NaN                                  4.89852  
4                                 NaN                                  4.74065

## Student Teacher Ratio For Primary Schools:

In [368]:
student_teacher_ratio_df = pd.read_csv('student_teacher_ratio.csv', encoding='latin-1')

In [369]:
student_teacher_ratio_df.head()

CountryÊ  Student teacher ratio, primary schoolÊ  Global rankÊ  Year
0  South Korea                                   29.71             1  1995
1       Mexico                                   28.71             2  1995
2       Turkey                                   27.75             3  1995
3     Colombia                                   24.81             4  1995
4      Ireland                                   23.32             5  1995

In [370]:
query = """
        SELECT
            CountryÊ AS Country,
            Year,
            "Student teacher ratio, primary schoolÊ" AS "Student teacher ratio, primary school"
        FROM student_teacher_ratio_df
        """

student_teacher_ratio_df = duckdb.sql(query).df()

In [371]:
student_teacher_ratio_df

Country  Year  Student teacher ratio, primary school
0    South Korea  1995                                  29.71
1         Mexico  1995                                  28.71
2         Turkey  1995                                  27.75
3       Colombia  1995                                  24.81
4        Ireland  1995                                  23.32
5       Slovakia  1995                                  21.98
6        Czechia  1995                                  20.19
7         France  1995                                  18.77
8      Australia  1995                                  18.15
9          Spain  1995                                  17.84
10       Germany  1995                                  17.46
11     Lithuania  1995                                  16.48
12        Canada  1995                                  16.23
13        Greece  1995                                  16.09
14      Slovenia  1995                                  15.07
15        Latvia  1995                                  13.17
16       Austria  1995                                  11.69
17       Hungary  1995                                  11.39
18         Italy  1995                                  10.97
19        Sweden  1995                                  10.52
20       Denmark  1995                                   9.94
21   South Korea  1996                                  28.39
22        Mexico  1996                                  28.34
23      Colombia  1996                                  25.36
24       Ireland  1996                                  22.54
25   New Zealand  1996                                  19.18
26       Czechia  1996                                  19.10
27        France  1996                                  18.74
28     Australia  1996                                  18.07
29       Germany  1996                                  17.04
30       Finland  1996                                  16.50
31        Canada  1996                                  16.48
32     Lithuania  1996                                  16.33
33        Greece  1996                                  14.96
34      Slovenia  1996                                  13.99
35        Latvia  1996                                  13.51
36       Austria  1996                                  12.45
37        Sweden  1996                                  11.21
38         Italy  1996                                  11.18
39   South Korea  1997                                  30.91
40        Mexico  1997                                  27.91
41       Ireland  1997                                  22.15
42        France  1997                                  18.96
43   New Zealand  1997                                  18.32
44     Australia  1997                                  17.88
45       Finland  1997                                  17.75
46       Germany  1997                                  17.19
47     Lithuania  1997                                  16.01
48        Greece  1997                                  13.94
49        Latvia  1997                                  13.48
50       Austria  1997                                  12.22
51       Hungary  1997                                  12.02
52        Sweden  1997                                  11.83
53         Chile  1998                                  33.23
54   South Korea  1998                                  30.90
55        Mexico  1998                                  27.57
56       Ireland  1998                                  25.84
57      Colombia  1998                                  23.29
58        France  1998                                  20.32
59   New Zealand  1998                                  19.43
60      Slovakia  1998                                  19.31
61        Canada  1998                                  17.95
62     Australia  1998                                  17.88
63       Czechia  1998                   

In [372]:
country_map = {"Australia":"AUS","Austria":"AUT","Belgium":"BEL",
            "Canada":"CAN", "Chile":"CHL", "Colombia":"COL",
            "Costa Rica":"CRI","Czechia":"CZE", 
            "Denmark":"DNK", "Estonia": "EST", 
            "Finland":"FIN", "France":"FRA", "Germany":"DEU", 
            "Greece":"GRC", "Hungary":"HUN", "Iceland":"ISL", 
            "Ireland":"IRL","Israel":"ISR", "Italy":"ITA", 
            "Japan":"JPN", "South Korea":"KOR",
            "Latvia":"LVA", "Lithuania":"LTU", "Luxembourg":"LUX", 
            "Mexico":"MEX", "Netherlands":"NLD", "New Zealand":"NZL",
            "Norway":"NOR", "Poland":"POL", "Portugal":"PRT", 
            "Slovakia":"SVK","Slovenia":"SVN","Spain":"ESP",
            "Sweden":"SWE","Switzerland":"CHE", "Turkey":"TUR",
            "UK":"UK","USA":"USA"}

In [373]:
student_teacher_ratio_df["Country"] = student_teacher_ratio_df["Country"].map(country_map)

In [374]:
student_teacher_ratio_df

Country  Year  Student teacher ratio, primary school
0       KOR  1995                                  29.71
1       MEX  1995                                  28.71
2       TUR  1995                                  27.75
3       COL  1995                                  24.81
4       IRL  1995                                  23.32
5       SVK  1995                                  21.98
6       CZE  1995                                  20.19
7       FRA  1995                                  18.77
8       AUS  1995                                  18.15
9       ESP  1995                                  17.84
10      DEU  1995                                  17.46
11      LTU  1995                                  16.48
12      CAN  1995                                  16.23
13      GRC  1995                                  16.09
14      SVN  1995                                  15.07
15      LVA  1995                                  13.17
16      AUT  1995                                  11.69
17      HUN  1995                                  11.39
18      ITA  1995                                  10.97
19      SWE  1995                                  10.52
20      DNK  1995                                   9.94
21      KOR  1996                                  28.39
22      MEX  1996                                  28.34
23      COL  1996                                  25.36
24      IRL  1996                                  22.54
25      NZL  1996                                  19.18
26      CZE  1996                                  19.10
27      FRA  1996                                  18.74
28      AUS  1996                                  18.07
29      DEU  1996                                  17.04
30      FIN  1996                                  16.50
31      CAN  1996                                  16.48
32      LTU  1996                                  16.33
33      GRC  1996                                  14.96
34      SVN  1996                                  13.99
35      LVA  1996                                  13.51
36      AUT  1996                                  12.45
37      SWE  1996                                  11.21
38      ITA  1996                                  11.18
39      KOR  1997                                  30.91
40      MEX  1997                                  27.91
41      IRL  1997                                  22.15
42      FRA  1997                                  18.96
43      NZL  1997                                  18.32
44      AUS  1997                                  17.88
45      FIN  1997                                  17.75
46      DEU  1997                                  17.19
47      LTU  1997                                  16.01
48      GRC  1997                                  13.94
49      LVA  1997                                  13.48
50      AUT  1997                                  12.22
51      HUN  1997                                  12.02
52      SWE  1997                                  11.83
53      CHL  1998                                  33.23
54      KOR  1998                                  30.90
55      MEX  1998                                  27.57
56      IRL  1998                                  25.84
57      COL  1998                                  23.29
58      FRA  1998                                  20.32
59      NZL  1998                                  19.43
60      SVK  1998                                  19.31
61      CAN  1998                                  17.95
62      AUS  1998                                  17.88
63      CZE  1998                                  17.67
64      FIN  1998                                  17.61
65      DEU  1998                                  17.44
66      ESP  1998                                  15.48
67      LVA  1998                                  15.45
68      LTU  1998                                  15.43
69      SVN  1

In [375]:
query = """
        SELECT *
        FROM combined_df
        LEFT JOIN student_teacher_ratio_df
        ON combined_df.Country = student_teacher_ratio_df.Country
        AND combined_df.Year = student_teacher_ratio_df.Year;
        """

combined_df = duckdb.sql(query).df()
combined_df.head()

Country  Year  GDP per Capita  Total Population  \
0     AUS  1995    22442.316842        18004882.0   
1     AUS  1996    23289.401829        18224767.0   
2     AUT  1995    23698.103090         7948278.0   
3     AUT  1998    26675.649686         7976789.0   
4     AUT  2003    32158.459529         8118245.0   

   Public Spending on Education (%)  Private Spending on Education (%)  \
0                               NaN                                NaN   
1                               NaN                                NaN   
2                               NaN                                NaN   
3                               NaN                                NaN   
4                               NaN                                NaN   

   Household Income per Capita  \
0                          NaN   
1                          NaN   
2                          NaN   
3                          NaN   
4                          NaN   

   Average Spending on Higher Education (USD/student)  Number of Universities  \
0                                                NaN                    187.0   
1                                                NaN                    187.0   
2                                                NaN                     84.0   
3                                                NaN                     84.0   
4                                                NaN                     84.0   

   Students per Teaching Staff  Primary Completion Rate (%)  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                    100.91772   
4                          NaN                          NaN   

   Upper Secondary Completion Rate (%)  Lower Secondary Completion Rate (%)  \
0                                  NaN                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                  NaN                                  NaN   

   Primary Enrollment rate (% gross)  Secondary Enrollment rate (% gross)  \
0                          101.29127                            143.23387   
1                          101.58029                            148.63600   
2                          102.36504                            106.58471   
3                          103.63034                             97.74473   
4                          100.46382                             99.47920   

   Tertiary Enrollment rate (% gross)  \
0                            70.68857   
1                            75.64778   
2                            44.97695   
3                            52.39628   
4                                 NaN   

   Government Expenditure On Education (%) Country_2  Year_2  \
0                                  5.13413       AUS  1995.0   
1                                  5.23100       AUS  1996.0   
2                                  5.42835       AUT  1995.0   
3                                  6.10374       AUT  1998.0   
4                                  5.36183       AUT  2003.0   

   Student teacher ratio, primary school  
0                                  18.15  
1                                  18.07  
2                                  11.69  
3                                  12.15  
4                                  13.18

In [376]:
combined_df

Country  Year  GDP per Capita  Total Population  \
0       AUS  1995    22442.316842      1.800488e+07   
1       AUS  1996    23289.401829      1.822477e+07   
2       AUT  1995    23698.103090      7.948278e+06   
3       AUT  1998    26675.649686      7.976789e+06   
4       AUT  2003    32158.459529      8.118245e+06   
5       AUT  2004    33784.446804      8.169441e+06   
6       AUT  2005    35024.557484      8.225278e+06   
7       AUT  2006    37662.888035      8.267948e+06   
8       AUT  2007    39437.038795      8.295189e+06   
9       AUT  2008    41316.022642      8.321541e+06   
10      AUT  2009    40927.556365      8.341483e+06   
11      AUT  2011    44469.209642      8.388534e+06   
12      AUT  2014    48813.534409      8.543932e+06   
13      AUT  2016    52665.087457      8.739806e+06   
14      AUT  2017    54188.360666      8.795073e+06   
15      BEL  2005    33176.680884      1.047862e+07   
16      BEL  2008    37883.233422      1.070911e+07   
17      BEL  2011    40943.343479      1.099361e+07   
18      BEL  2012    42290.477674      1.106775e+07   
19      BEL  2013    43672.712292      1.112503e+07   
20      BEL  2014    44929.933328      1.117978e+07   
21      BEL  2015    46201.685891      1.123847e+07   
22      BEL  2016    48599.202676      1.129500e+07   
23      BEL  2017    50442.947518      1.134908e+07   
24      CAN  1995    23485.643444      2.930231e+07   
25      CAN  1998    26319.930258      3.015517e+07   
26      CAN  1999    27841.629576      3.040129e+07   
27      CAN  2000    29362.289573      3.068573e+07   
28      CHE  2012    59440.934085      7.996861e+06   
29      CHE  2013    61656.490978      8.089346e+06   
30      CHE  2016    67350.735189      8.373334e+06   
31      CHE  2017    68193.502958      8.451834e+06   
32      CHL  1998     8927.892867      1.497490e+07   
33      CHL  1999     8909.771365      1.516235e+07   
34      CHL  2000     9440.041965      1.534333e+07   
35      CHL  2002    10205.704047      1.569170e+07   
36      CHL  2003    10779.638668      1.585698e+07   
37      CHL  2005    12600.905817      1.618349e+07   
38      CHL  2007    16771.182748      1.651793e+07   
39      CHL  2008    16449.614266      1.669775e+07   
40      CHL  2010    18041.314313      1.706393e+07   
41      CHL  2011    20235.570348      1.725416e+07   
42      CHL  2013    22295.740021      1.761190e+07   
43      CHL  2014    22650.712398      1.778762e+07   
44      CHL  2015    22563.582179      1.797142e+07   
45      COL  1998     7022.024884      3.801236e+07   
46      COL  1999     6658.492888      3.858502e+07   
47      COL  2000     6886.405819      3.914008e+07   
48      COL  2002     7265.177903      4.019068e+07   
49      COL  2004     8127.579576      4.118809e+07   
50      COL  2005     8676.107355      4.167188e+07   
51      COL  2006     9433.241822      4.217013e+07   
52      COL  2007    10228.188007      4.265863e+07   
53      COL  2008    10651.506633      4.313402e+07   
54      COL  2010    11206.221832      4.408629e+07   
55      COL  2011    12108.234854      4.455342e+07   
56      COL  2013    13266.002148      4.543494e+07   
57      COL  2014    13777.241959      4.586601e+07   
58      COL  2015    13762.750912      4.631390e+07   
59      COL  2016    14514.224389      4.683012e+07   
60      COL  2017    14930.865719      4.741920e+07   
61      COL  2018    15814.696386      4.825849e+07   
62      CZE  1995    13855.325028      1.033076e+07   
63      CZE  1996    14689.582503      1.031535e+07   
64      CZE  1998    14977.240849      1.029494e+07   
65      CZE  1999    15397.922823      1.028278e+07   
66      CZE  2000    16211.043497      1.027250e+07   
67      CZE  2001    17611.358497      1.022419e+07   
68      CZE  2002    18245.669005      1.020077e+07   
69      CZE  2004    20912.054683      1.020692e+07   
70      CZE  2005    22045.998880      1.023409e+07   
71      CZE  2006    23857.518264      1.026

In [377]:
# Fill missing values in Country with values from Country_2
combined_df['Country'] = combined_df['Country'].fillna(combined_df['Country_2'])

# Fill missing values in Country_2 with values from Country
combined_df['Country_2'] = combined_df['Country_2'].fillna(combined_df['Country'])

# Fill missing values in Year with values from Year_2
combined_df['Year'] = combined_df['Year'].fillna(combined_df['Year_2'])

# Fill missing values in Year_2 with values from Year
combined_df['Year_2'] = combined_df['Year_2'].fillna(combined_df['Year'])

#dropping Country_2 and Year_2 columns
combined_df = combined_df.drop(columns=['Country_2', 'Year_2'])

#making the values in the Year column integers
combined_df['Year'] = combined_df['Year'].astype(int)

combined_df.head()

Country  Year  GDP per Capita  Total Population  \
0     AUS  1995    22442.316842        18004882.0   
1     AUS  1996    23289.401829        18224767.0   
2     AUT  1995    23698.103090         7948278.0   
3     AUT  1998    26675.649686         7976789.0   
4     AUT  2003    32158.459529         8118245.0   

   Public Spending on Education (%)  Private Spending on Education (%)  \
0                               NaN                                NaN   
1                               NaN                                NaN   
2                               NaN                                NaN   
3                               NaN                                NaN   
4                               NaN                                NaN   

   Household Income per Capita  \
0                          NaN   
1                          NaN   
2                          NaN   
3                          NaN   
4                          NaN   

   Average Spending on Higher Education (USD/student)  Number of Universities  \
0                                                NaN                    187.0   
1                                                NaN                    187.0   
2                                                NaN                     84.0   
3                                                NaN                     84.0   
4                                                NaN                     84.0   

   Students per Teaching Staff  Primary Completion Rate (%)  \
0                          NaN                          NaN   
1                          NaN                          NaN   
2                          NaN                          NaN   
3                          NaN                    100.91772   
4                          NaN                          NaN   

   Upper Secondary Completion Rate (%)  Lower Secondary Completion Rate (%)  \
0                                  NaN                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                  NaN                                  NaN   

   Primary Enrollment rate (% gross)  Secondary Enrollment rate (% gross)  \
0                          101.29127                            143.23387   
1                          101.58029                            148.63600   
2                          102.36504                            106.58471   
3                          103.63034                             97.74473   
4                          100.46382                             99.47920   

   Tertiary Enrollment rate (% gross)  \
0                            70.68857   
1                            75.64778   
2                            44.97695   
3                            52.39628   
4                                 NaN   

   Government Expenditure On Education (%)  \
0                                  5.13413   
1                                  5.23100   
2                                  5.42835   
3                                  6.10374   
4                                  5.36183   

   Student teacher ratio, primary school  
0                                  18.15  
1                                  18.07  
2                                  11.69  
3                                  12.15  
4                                  13.18